## **Imports**

In [197]:
import pandas as pd
import numpy as np
import importlib
from application.modeling import disbursements
from application.modeling import interest_income
from application.modeling import other_income
from application.modeling import helper
from application.modeling import depreciation
from application.modeling import expenses
from application.modeling import income_statement
from application.modeling import direct_cashflow
from application.modeling import balance_sheet
from application.modeling import statement_of_cashflows
from application.modeling import loan_book
from application.modeling import borrowings

pd.options.display.max_columns = None
pd.options.display.max_rows = 100
pd.options.display.float_format = "{:,.2f}".format

## **Inputs**

In [213]:
start_date = "2023-09"
months_to_forecast = 12
imtt = 0.01

In [214]:
importlib.reload(helper)

<module 'application.modeling.helper' from 'c:\\Users\\HP\\Desktop\\Claxon\\Budgeting\\manage-tenants-template\\application\\modeling\\helper.py'>

In [215]:
disbursement_parameters = pd.read_csv("./data_templates/disbursement_parameters.csv", index_col=0)
disbursement_parameters = helper.match_months_to_forecast_with_df(
    df=disbursement_parameters,
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)

disbursement_parameters.head()

Sep-2023  Oct-2023  Nov-2023  Dec-2023  \
AGENT_COMMISSION                  0.05      0.05      0.05      0.05   
AGENT_CONTRIBUTION_PERCENT        0.10      0.10      0.10      0.10   
BUSINESS_ACQUISITION_PERCENT      0.03      0.03      0.03      0.03   
CREDIT_OFFICER_COMMISSION         0.01      0.01      0.01      0.01   
CREDIT_OFFICER_SALARY           600.00    600.00    600.00    600.00   

                              Jan-2024  Feb-2024  Mar-2024  Apr-2024  \
AGENT_COMMISSION                  0.05      0.05      0.05      0.05   
AGENT_CONTRIBUTION_PERCENT        0.10      0.10      0.10      0.10   
BUSINESS_ACQUISITION_PERCENT      0.03      0.03      0.03      0.03   
CREDIT_OFFICER_COMMISSION         0.01      0.01      0.01      0.01   
CREDIT_OFFICER_SALARY           600.00    600.00    600.00    600.00   

                              May-2024  Jun-2024  Jul-2024  Aug-2024  
AGENT_COMMISSION                  0.05      0.05      0.05      0.05  
AGENT_CONTRIBUTION_PERCENT        0.10      0.10      0.10      0.10  
BUSINESS_ACQUISITION_PERCENT      0.03      0.03      0.03      0.03  
CREDIT_OFFICER_COMMISSION         0.01      0.01      0.01      0.01  
CREDIT_OFFICER_SALARY           600.00    600.00    600.00    600.00

In [217]:
other_parameters = pd.read_csv("./data_templates/other_parameters.csv", index_col=0)
other_parameters = helper.match_months_to_forecast_with_df(
    df=other_parameters,
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)
other_parameters

Sep-2023  Oct-2023  Nov-2023  \
NEW_INVENTORY                                    0.00      0.00      0.00   
INVENTORY_USED                                   0.00      0.00      0.00   
NEW_INTERGROUP_RECEIVABLES                       0.00      0.00      0.00   
NEW_OTHER_PAYABLES                               0.00      0.00      0.00   
NEW_OTHER_RECEIVABLES                            0.00      0.00      0.00   
NEW_TRADE_PAYABLES                               0.00      0.00      0.00   
NEW_TRADE_RECEIVABLES                            0.00 91,225.40 57,639.36   
PAYMENTS_TO_OTHER_PAYABLES                       0.00      0.00      0.00   
PAYMENTS_TO_TRADE_PAYABLES                       0.00 13,404.72 68,786.66   
RECEIPTS_FROM_TRADE_RECEIVABLES                  0.00      0.00      0.00   
RECEIPTS_FROM_OTHER_RECEIVABLES                  0.00      0.00      0.00   
RECEIPTS_FROM_INTERGROUP_RECEIVABLES             0.00      0.00      0.00   
NaN                                               NaN       NaN       NaN   
INTANGIBLE_ASSETS                                0.00      0.00      0.00   
INVESTMENT_IN_SUBSIDIARIES                       0.00      0.00      0.00   
INVESTMENT_IN_ASSOCIATES                         0.00      0.00      0.00   
INVESTMENT_PROPERTIES                            0.00      0.00      0.00   
EQUITY_INVESTMENTS                               0.00      0.00      0.00   
LONG_TERM_MONEY_MARKET_INVESTMENTS               0.00      0.00      0.00   
SHORT_TERM_MONEY_MARKET_INVESTMENTS              0.00      0.00      0.00   
LOANS_TO_RELATED_ENTITIES                        0.00      0.00      0.00   
NaN                                               NaN       NaN       NaN   
TREASURY_SHARES                                  0.00      0.00      0.00   
INTERCOMPANY_LOANS                               0.00      0.00      0.00   
SHARE_CAPITAL                                    0.00   -919.54   -908.18   
SHARE_PREMIUM                                    0.00    -14.35    -14.17   
OTHER_COMPONENTS_OF_EQUITY                       0.00      0.00      0.00   
NaN                                               NaN       NaN       NaN   
TREASURY_MOVEMENTS                               0.00      0.00      0.00   
INTEREST_EXPENSE_ACCRUED                         0.00      0.00      0.00   
OTHER_NON_CASH_ITEMS                             0.00      0.00      0.00   
DIVIDEND_PAID                                    0.00      0.00      0.00   
PROVISION_FOR_TAX                                0.00      0.00      0.00   
INFLATION_RATE                                   0.05      0.05      0.05   
OTHER_STAFF_SALARY                          17,000.00 17,000.00 17,000.00   
PENSION_AND_STATUROTY_CONTRIBUTIONS_PERCENT      0.11      0.11      0.11   
TAX_RATE                                         0.25      0.25      0.25   

                                             Dec-2023     Jan-2024  Feb-2024  \
NEW_INVENTORY                                    0.00         0.00      0.00   
INVENTORY_USED                                   0.00         0.00      0.00   
NEW_INTERGROUP_RECEIVABLES                       0.00         0.00      0.00   
NEW_OTHER_PAYABLES                               0.00         0.00      0.00   
NEW_OTHER_RECEIVABLES                            0.00         0.00      0.00   
NEW_TRADE_PAYABLES                               0.00         0.00 15,888.40   
NEW_TRADE_RECEIVABLES                       58,279.67         0.00 27,773.92   
PAYMENTS_TO_OTHER_PAYABLES                       0.00         0.00      0.00   
PAYMENTS_TO_TRADE_PAYABLES                  80,963.15   466,687.36      0.00   
RECEIPTS_FROM_TRADE_RECEIVABLES                  0.00 1,187,638.92      0.00   
RECEIPTS_FROM_OTHER_RECEIVABLES                  0.00         0.00      0.00   
RECEIPTS_FROM_INTERGROUP_RECEIVABLES             0.00         0.00      0.00   
NaN                                               NaN          NaN       NaN  

In [218]:
details_of_assets = pd.read_csv("./data_templates/details_of_assets.csv")
details_of_assets.head()

Asset ID Acquisition Date  \r\nLife  \r\nBook Value  \r\nNet Value  \
0  CE-HRE-0039       15/11/2017        10             261         106.60   
1  CE-HRE-0040       15/11/2017        10             261         106.60   
2  CE-HRE-0041       15/11/2017        10             261         106.60   
3  CE-HRE-0042       15/11/2017        10             261         106.60   
4  CE-HRE-0043       15/11/2017        10             261         106.60   

   Salvage Value         Method  Depreciation  
0              0  straight_line           NaN  
1              0  straight_line           NaN  
2              0  straight_line           NaN  
3              0  straight_line           NaN  
4              0  straight_line           NaN

In [219]:
details_of_long_term_borrowing = pd.read_csv("./data_templates/details_of_long_term_borrowing.csv")
details_of_long_term_borrowing.head()

Effective Date            Institution  Nominal Amount   Interest Rate  \
0     31/12/2022  ZIMNAT LIFE ASSURANCE           376455           0.06   
1     06/05/2022              MASAWARA              5613           0.06   
2     31/12/2022                Grandre           160000           0.06   
3     31/12/2022                MINERVA            15000           0.08   
4     10/09/2022              ZAM-CARGO           364000           0.05   

   Tenure               Repayment Frequency  Frequency            Method  
0      60                    Monthly (P+I)          12  reducing_balance  
1      60                    Monthly (P+I)          12  reducing_balance  
2      36            Quaterly (I+Bullet P)           4     straight_line  
3      36                     Bullet (P+I)           0     straight_line  
4      36   Annually(I) Principal rollover          12     straight_line

In [220]:
details_of_short_term_borrowing = pd.read_csv("./data_templates/details_of_short_term_borrowing.csv")
details_of_short_term_borrowing.head()

Effective Date             Institution  Nominal Amount   Interest Rate  \
0     24/04/2023                     FCB       120,383.84           0.18   
1     02/03/2023  ZIMNAT LIFE ASSURANCE         50,000.00           0.14   
2     31/12/2022   Zimnat Life Assurance        20,000.00           0.08   
3     31/12/2022                 Grandre       100,000.00           0.12   
4     23/04/2023                     FCB        18,429.93           1.50   

   Tenure               Repayment Frequency  Frequency            Method  
0       3                     Bullet (P+I)           0     straight_line  
1       6                    Monthly (P+I)          12  reducing_balance  
2      12   Annually(I) Principal rollover           1     straight_line  
3      12            Quaterly (I+Bullet P)           4     straight_line  
4      12                     Bullet (P+I)           0     straight_line

In [221]:
expenses_certain = pd.read_csv("./data_templates/expenses_certain.csv", index_col=0)

expenses_certain = helper.match_months_to_forecast_with_df(
    df=expenses_certain,
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)

expenses_certain.head()

Sep-2023  Oct-2023  Nov-2023  Dec-2023  Jan-2024  Feb-2024  \
Training            40.00     40.00  6,840.00  1,740.00  1,540.00  2,540.00   
CILL                 0.00      0.00      0.00      0.00      0.00      0.00   
Bonus Provision  2,023.00  2,023.00  2,023.00  2,160.50  2,577.17  2,577.17   
Retrenchments        0.00      0.00      0.00      0.00      0.00      0.00   
Staff Welfare   17,275.00 17,275.00 17,275.00 17,275.00 17,275.00 17,706.88   

                 Mar-2024  Apr-2024  May-2024  Jun-2024  Jul-2024  Aug-2024  
Training         1,540.00     40.00  2,640.00     40.00     40.00     40.00  
CILL                 0.00      0.00      0.00      0.00      0.00      0.00  
Bonus Provision  2,906.33  3,056.33  3,056.33  3,189.67  3,189.67  3,189.67  
Retrenchments        0.00      0.00      0.00      0.00      0.00      0.00  
Staff Welfare   17,706.88 17,706.88 17,706.88 17,706.88 17,706.88 18,052.38

In [222]:
expenses_uncertain = pd.read_csv("./data_templates/expenses_uncertain.csv", index_col=0)
expenses_uncertain = helper.match_months_to_forecast_with_df(
    df=expenses_uncertain,
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)
expenses_uncertain.head()

Sep-2023  Oct-2023  Nov-2023  Dec-2023  Jan-2024  Feb-2024  Mar-2024  \
nothing         0         0         0         0         0         0         0   

         Apr-2024  May-2024  Jun-2024  Jul-2024  Aug-2024  
nothing         0         0         0         0         0

In [223]:
opening_balances = pd.read_csv("./data_templates/opening_balances.csv")
opening_balances

TRADE_RECEIVABLES  TRADE_PAYABLES  CASH_ON_HAND  ISSUED_SHARE_CAPITAL  \
0            1092458          938595        331856                  7050   

   SHARE_PREMIUM  OTHER_COMPONENTS_OF_EQUITY  TREASURY_SHARES  \
0            110                       59784                0   

   RETAINED_EARNINGS  INTERCOMPANY_LOANS  DEFERED_TAXATION  OTHER_RECEIVABLES  \
0             876511                   0                 0                  0   

   OTHER_PAYABLES  PROVISION_FOR_TAXATION  PROVISION_FOR_CREDIT_LOSS  \
0               0                       0                          0   

   INVESTMENT_IN_SUBSIDIARIES  INVESTMENT_IN_ASSOCIATES  \
0                           0                         0   

   INVESTMENT_PROPERTIES  EQUITY_INVESTMENTS  \
0                      0                   0   

   LONG_TERM_MONEY_MARKET_INVESTMENTS  LOANS_TO_RELATED_ENTITIES  \
0                                   0                          0   

   TREASURY_SHARES.1  INTANGIBLE_ASSETS  INVENTORIES  OTHER_RECEIVABLES.1  \
0                  0                  0            0                    0   

   INTERGROUP_RECEIVABLES  SHORT_TERM_MONEY_MARKET_INVESTMENTS  
0                       0                                    0

In [224]:
existing_loans = pd.read_csv("./data_templates/existing_loans.csv")
existing_loans.head()

Loan Number  Disbursement Date  Loan Term  Loan Amount  \
0  100,120,644,000,001        13/10/2021         60    20,000.00   
1  100,120,644,000,002        15/10/2021         60    12,000.00   
2  100,120,644,000,003        25/10/2021         60    20,000.00   
3  100,120,644,000,004        26/10/2021         60    20,000.00   
4  100,120,644,000,005        28/10/2021         60    20,000.00   

   Closing Balance  Interest Rate  Admin Fee  Credit Insurance Fee Loan Type  
0       -14,769.50           0.00       0.02                  0.02       B2B  
1        -8,855.52           0.00       0.02                  0.02       B2B  
2       -14,708.39           0.00       0.02                  0.02       B2B  
3       -14,703.34           0.00       0.02                  0.02       B2B  
4       -14,693.08           0.00       0.02                  0.02       B2B

## **New Disbursements**

In [225]:
new_disbursements_df  = disbursements.calculate_new_disbursements(disbursement_parameters=disbursement_parameters)
new_disbursements_df.head()

b2b_disbursements  sme_disbursements  consumer_ssb_disbursements  \
Sep-2023          57,011.05         360,000.00                   48,000.00   
Oct-2023          27,480.25         384,000.00                   60,000.00   
Nov-2023          27,480.25         432,000.00                   72,000.00   
Dec-2023          34,900.00         342,000.00                   80,000.00   
Jan-2024          66,173.00         513,000.00                   96,000.00   

          consumer_pvt_disbursements        total  
Sep-2023                   96,000.00   609,011.05  
Oct-2023                  120,000.00   651,480.25  
Nov-2023                  172,800.00   805,080.25  
Dec-2023                  216,000.00   808,900.00  
Jan-2024                  259,200.00 1,097,573.00

### **Calculate Repayment Amount For New Disbursements**

In [226]:
monthly_repayment_new_disbursements_df = (
    interest_income.calculate_monthly_repayments_new_disbursements(
        new_disbursements_df=new_disbursements_df,
        disbursement_parameters=disbursement_parameters,
    )
)
monthly_repayment_new_disbursements_df.head()

sme_monthly_repayment  b2b_monthly_repayment  \
Sep-2023              81,451.18               5,779.79   
Oct-2023              86,881.26               2,785.95   
Nov-2023              97,741.42               2,785.95   
Dec-2023              77,378.62               3,538.17   
Jan-2024             116,067.93               6,708.63   

          consumer_ssb_monthly_repayment  consumer_pvt_monthly_repayment  \
Sep-2023                        8,006.34                       16,012.68   
Oct-2023                       10,007.93                       20,015.86   
Nov-2023                       12,009.51                       28,822.83   
Dec-2023                       13,343.90                       36,028.54   
Jan-2024                       16,012.68                       43,234.25   

              total  
Sep-2023 111,250.00  
Oct-2023 119,691.00  
Nov-2023 141,359.72  
Dec-2023 130,289.24  
Jan-2024 182,023.50

### **Generate Loan Schedules For New Disbursements**

In [227]:
loan_schedules_for_all_new_disbursements = (
    interest_income.generate_loan_schedules_for_all_new_disbursements(
        new_disbursements_df=new_disbursements_df,
        disbursement_parameters=disbursement_parameters,
        monthly_repayment_new_disbursements_df=monthly_repayment_new_disbursements_df,
        months_to_forecast=months_to_forecast,
    )
)
loan_schedules_for_all_new_disbursements.keys()

dict_keys(['sme_loan_schedules', 'b2b_loan_schedules', 'consumer_ssb_loan_schedules', 'consumer_pvt_loan_schedules'])

### **Capital Repayment New Disbursement**

In [228]:
capital_repayment_new_disbursements_df = interest_income.generate_capital_repayment_new_disbursements_df(
    loan_schedules_for_all_new_disbursements=loan_schedules_for_all_new_disbursements
)
capital_repayment_new_disbursements_df.head()

sme_capital_repayments  b2b_capital_repayments  \
Oct-2023               47,251.18                5,637.26   
Nov-2023              102,141.30                8,368.61   
Dec-2023              168,546.15               11,106.78   
Jan-2024              229,446.65               14,585.46   
Feb-2024              318,577.02               21,165.12   

          consumer_pvt_capital_repayments  consumer_ssb_capital_repayments  \
Oct-2023                         7,372.68                         3,686.34   
Nov-2023                        17,252.08                         8,626.04   
Dec-2023                        32,075.60                        14,931.90   
Jan-2024                        51,550.95                        22,419.67   
Feb-2024                        76,096.78                        31,810.13   

              total  
Oct-2023  63,947.47  
Nov-2023 136,388.03  
Dec-2023 226,660.43  
Jan-2024 318,002.74  
Feb-2024 447,649.05

### **Interest Income New Disbursements**


In [229]:
interest_income_new_disbursements_df = interest_income.generate_interest_income_new_disbursements_df(
    loan_schedules_for_all_new_disbursements=loan_schedules_for_all_new_disbursements
)

interest_income_new_disbursements_df.head()

sme_interest_income  b2b_interest_income  \
Oct-2023            34,200.00               142.53   
Nov-2023            66,191.14               197.14   
Dec-2023            97,527.71               244.91   
Jan-2024           114,005.83               304.40   
Feb-2024           140,943.40               433.37   

          consumer_pvt_interest_income  consumer_ssb_interest_income  \
Oct-2023                      8,640.00                      4,320.00   
Nov-2023                     18,776.46                      9,388.23   
Dec-2023                     32,775.77                     15,091.89   
Jan-2024                     49,328.97                     20,948.01   
Feb-2024                     68,017.38                     27,570.24   

              total  
Oct-2023  47,302.53  
Nov-2023  94,552.96  
Dec-2023 145,640.28  
Jan-2024 184,587.21  
Feb-2024 236,964.39

### **Calculate Admin Fee On New Disbursements**

In [230]:
admin_fee_for_all_new_disbursements_df = other_income.calculate_admin_fee_for_all_new_disbursements(
    new_disbursements_df=new_disbursements_df,
    disbursement_parameters=disbursement_parameters,
    months_to_forecast=months_to_forecast,
)

admin_fee_for_all_new_disbursements_df.head()

sme_admin_fee  b2b_admin_fee  consumer_ssb_admin_fee  \
Sep-2023       3,000.00         114.02                  240.00   
Oct-2023       6,200.00         168.98                  540.00   
Nov-2023       9,800.00         223.94                  900.00   
Dec-2023      12,650.00         293.74                1,300.00   
Jan-2024      16,925.00         426.09                1,780.00   

          consumer_pvt_admin_fee     total  
Sep-2023                  480.00  3,834.02  
Oct-2023                1,080.00  7,988.98  
Nov-2023                1,944.00 12,867.94  
Dec-2023                3,024.00 17,267.74  
Jan-2024                4,320.00 23,451.09

### **Calculate Credit Life Insurance On New Disbursement**

In [231]:
credit_insurance_fee_for_all_new_disbursements_df = other_income.calculate_credit_insurance_fee_for_all_new_disbursements(
        new_disbursements_df=new_disbursements_df,
        disbursement_parameters=disbursement_parameters,
        months_to_forecast=months_to_forecast,
    )

credit_insurance_fee_for_all_new_disbursements_df.head()

sme_credit_insurance_fee  b2b_credit_insurance_fee  \
Sep-2023                  1,200.00                     96.92   
Oct-2023                  2,480.00                    143.64   
Nov-2023                  3,920.00                    190.35   
Dec-2023                  5,060.00                    249.68   
Jan-2024                  6,770.00                    362.18   

          consumer_ssb_credit_insurance_fee  \
Sep-2023                              96.00   
Oct-2023                             216.00   
Nov-2023                             360.00   
Dec-2023                             520.00   
Jan-2024                             712.00   

          consumer_pvt_credit_insurance_fee    total  
Sep-2023                             192.00 1,584.92  
Oct-2023                             432.00 3,271.64  
Nov-2023                             777.60 5,247.95  
Dec-2023                           1,209.60 7,039.28  
Jan-2024                           1,728.00 9,572.18

### **Calculate For Credit Loss For New Disbursements**

In [232]:
provision_for_credit_loss_for_all_new_disbursements = (
    expenses.calculate_provision_for_credit_loss_for_all_new_disbursements(
        new_disbursements_df=new_disbursements_df, disbursement_parameters=disbursement_parameters
    )
)

provision_for_credit_loss_for_all_new_disbursements.head()

sme_provision_for_credit_loss  b2b_provision_for_credit_loss  \
Sep-2023                       5,400.00                           0.00   
Oct-2023                       5,760.00                           0.00   
Nov-2023                       4,320.00                           0.00   
Dec-2023                       3,420.00                           0.00   
Jan-2024                       5,130.00                           0.00   

          consumer_ssb_provision_for_credit_loss  \
Sep-2023                                  960.00   
Oct-2023                                1,200.00   
Nov-2023                                1,440.00   
Dec-2023                                1,600.00   
Jan-2024                                1,920.00   

          consumer_pvt_provision_for_credit_loss    total  
Sep-2023                                  960.00 7,320.00  
Oct-2023                                1,200.00 8,160.00  
Nov-2023                                1,728.00 7,488.00  
Dec-2023                                1,728.00 6,748.00  
Jan-2024                                2,073.60 9,123.60

## **Existing Loans**

### **Generate Loan Schedules For Existing Loans**


In [233]:
existing_loans = helper.columns_to_snake_case(existing_loans)
existing_loans = existing_loans.loc[existing_loans["closing_balance"] > 0]

In [234]:
existing_loans.head()

loan_number disbursement_date  loan_term  loan_amount  \
25  100,120,692,000,003        16/04/2021         36    20,000.00   
27  100,120,692,000,005        16/04/2021         36    20,000.00   
29  100,120,692,000,007        02/02/2022         36    20,000.00   
33  100,120,692,000,011        19/07/2022         36    19,352.00   
73  100,120,692,000,016        05/04/2023          6       800.00   

    closing_balance  interest_rate  admin_fee  credit_insurance_fee loan_type  
25            84.65           0.00       0.02                  0.02       B2B  
27             6.08           0.00       0.02                  0.02       B2B  
29           121.27           0.00       0.02                  0.02       B2B  
33           164.30           0.00       0.02                  0.02       B2B  
73           275.45           0.00       0.02                  0.02       B2B

In [236]:
existing_loans_schedules = borrowings.calculate_reducing_balance_loans_schedules(
    interest_rates=existing_loans["interest_rate"],
    effective_dates=existing_loans["disbursement_date"],
    frequencies=(existing_loans['interest_rate']*0+12),
    loan_identifiers=existing_loans["loan_number"],
    tenures=existing_loans["loan_term"],
    amounts=existing_loans["loan_amount"],
    is_interest_rate_annual=False
)

existing_loans_schedules.keys()

dict_keys(['outstanding_balance_at_start', 'capital_repayments', 'interest_payments', 'repayments'])

In [24]:
existing_loans_schedules_outstanding_balances_df = existing_loans_schedules["outstanding_balance_at_start"]

### **Capital Repayment for Existing Loans**

In [25]:
capital_repayment_existing_loans = existing_loans_schedules['capital_repayments'].sum()
capital_repayment_existing_loans.loc[helper.generate_columns(start_date=start_date, period=12)]

Sep-2023   59,655.62
Oct-2023   10,092.45
Nov-2023    6,747.14
Dec-2023    4,764.47
Jan-2024    2,982.53
Feb-2024    2,973.78
Mar-2024    2,659.76
Apr-2024    2,630.20
May-2024    1,473.53
Jun-2024    1,477.22
Jul-2024    1,480.91
Aug-2024    1,484.61
dtype: float64

### **Intererest Income For Existing Loans**

In [26]:
interest_income_existing_loans = existing_loans_schedules['interest_payments'].sum()
interest_income_existing_loans.loc[helper.generate_columns(start_date,12)]

Sep-2023   6,626.19
Oct-2023   1,283.41
Nov-2023     637.27
Dec-2023     296.86
Jan-2024     143.96
Feb-2024     103.96
Mar-2024      65.31
Apr-2024      55.50
May-2024      48.93
Jun-2024      45.24
Jul-2024      41.55
Aug-2024      37.85
dtype: float64

### **Calculate Other Income Existing Loans**

In [27]:
existing_loans = helper.columns_to_snake_case(existing_loans)
existing_loans = existing_loans.loc[existing_loans["closing_balance"] > 0]

In [28]:
other_income_existing_loans_df = other_income.calculate_other_income_existing_loans(
    existing_loans=existing_loans,
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)
other_income_existing_loans_df.head()

credit_insurance_fee_existing_loans  admin_fee_existing_loans  total
May-2021                                55.01                    167.36 222.37
Jun-2021                               111.68                    395.03 506.71
Jul-2021                               111.68                    395.03 506.71
Aug-2021                                83.35                    281.19 364.54
Sep-2021                                83.35                    281.19 364.54

## **Interest Income**

In [29]:
total_interest_income = interest_income.aggregate_new_and_existing_loans_interest_income(
    interest_income_new_disbursements_df=interest_income_new_disbursements_df,
    interest_income_existing_loans= interest_income_existing_loans,
    start_date= start_date, 
    months_to_forecast= months_to_forecast
)
total_interest_income.head()

Sep-2023     6,626.19
Oct-2023    48,585.94
Nov-2023    95,190.23
Dec-2023   145,937.14
Jan-2024   184,731.17
dtype: float64

## **Other Income**

In [30]:
other_income_df = other_income.aggregate_other_income(
    admin_fee_for_all_new_disbursements_df=admin_fee_for_all_new_disbursements_df,
    admin_fee_existing_loans=other_income_existing_loans_df['admin_fee_existing_loans'],
    credit_insurance_fee_existing_loans=other_income_existing_loans_df['credit_insurance_fee_existing_loans'],
    credit_insurance_fee_for_all_new_disbursements_df=credit_insurance_fee_for_all_new_disbursements_df, 
    start_date=start_date, 
    months_to_forecast=months_to_forecast
)
other_income_df.head()

admin_fee  credit_insurance_fee     total
Sep-2023   7,599.28              3,170.29 10,769.57
Oct-2023  15,745.56              6,478.27 22,223.83
Nov-2023  25,280.94             10,341.89 35,622.82
Dec-2023  33,811.44             13,816.91 47,628.35
Jan-2024  45,844.39             18,744.33 64,588.72

## **Depreciation**

In [31]:
details_of_assets = helper.columns_to_snake_case(details_of_assets)
details_of_assets.head()

asset_id acquisition_date  life  book_value  net_value  salvage_value  \
0  CE-HRE-0039       15/11/2017    10         261     106.60              0   
1  CE-HRE-0040       15/11/2017    10         261     106.60              0   
2  CE-HRE-0041       15/11/2017    10         261     106.60              0   
3  CE-HRE-0042       15/11/2017    10         261     106.60              0   
4  CE-HRE-0043       15/11/2017    10         261     106.60              0   

          method  depreciation  
0  straight_line           NaN  
1  straight_line           NaN  
2  straight_line           NaN  
3  straight_line           NaN  
4  straight_line           NaN

In [32]:
depreciations_and_nbvs = depreciation.calculate_depreciations_and_nbvs(
    details_of_assets=details_of_assets,
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)
depreciations_and_nbvs.keys()

dict_keys(['nbvs', 'dpns'])

## **Salaries**

In [33]:
salaries_and_pension_and_statutory_contributions_df = (
    expenses.calculate_salaries_and_pension_and_statutory_contributions(
        new_disbursements_df=new_disbursements_df,
        disbursement_parameters=disbursement_parameters,
        other_parameters = other_parameters, 
        months_to_forecast=months_to_forecast,
        start_date=start_date,
    )
)
salaries_and_pension_and_statutory_contributions_df.head()

agent_commission  credit_officer_salaries  \
Sep-2023          7,200.00                 3,600.00   
Oct-2023          9,000.00                 3,600.00   
Nov-2023         12,240.00                 3,600.00   
Dec-2023         14,800.00                 3,600.00   
Jan-2024         17,760.00                 5,400.00   

          credit_officer_commission  other_staff_salaries     total  \
Sep-2023                   3,600.00             17,000.00 31,400.00   
Oct-2023                   3,840.00             17,000.00 33,440.00   
Nov-2023                   4,320.00             17,000.00 37,160.00   
Dec-2023                   3,420.00             17,000.00 38,820.00   
Jan-2024                   5,130.00             17,000.00 45,290.00   

          pensions_and_statutory_contributions  
Sep-2023                              2,340.16  
Oct-2023                              2,340.16  
Nov-2023                              2,340.16  
Dec-2023                              2,340.16  
Jan-2024                              2,544.64

## **Provisions**


In [34]:
provision_for_credit_loss_for_all_new_disbursements_df = (
    expenses.calculate_provision_for_credit_loss_for_all_new_disbursements(
        new_disbursements_df=new_disbursements_df,
        disbursement_parameters=disbursement_parameters,
    )
)
provision_for_credit_loss_for_all_new_disbursements_df.head()

sme_provision_for_credit_loss  b2b_provision_for_credit_loss  \
Sep-2023                       5,400.00                           0.00   
Oct-2023                       5,760.00                           0.00   
Nov-2023                       4,320.00                           0.00   
Dec-2023                       3,420.00                           0.00   
Jan-2024                       5,130.00                           0.00   

          consumer_ssb_provision_for_credit_loss  \
Sep-2023                                  960.00   
Oct-2023                                1,200.00   
Nov-2023                                1,440.00   
Dec-2023                                1,600.00   
Jan-2024                                1,920.00   

          consumer_pvt_provision_for_credit_loss    total  
Sep-2023                                  960.00 7,320.00  
Oct-2023                                1,200.00 8,160.00  
Nov-2023                                1,728.00 7,488.00  
Dec-2023                                1,728.00 6,748.00  
Jan-2024                                2,073.60 9,123.60

## **Calculating Finance Costs**

In [35]:
importlib.reload(borrowings)

<module 'application.modeling.borrowings' from 'c:\\Users\\HP\\Desktop\\Claxon\\Budgeting\\manage-tenants-template\\application\\modeling\\borrowings.py'>

In [36]:
details_of_short_term_borrowings = helper.columns_to_snake_case(
    details_of_short_term_borrowing
)
details_of_long_term_borrowings = helper.columns_to_snake_case(
    details_of_long_term_borrowing
)

In [37]:
details_of_long_term_borrowing

effective_date             institution  nominal_amount  interest_rate  \
0     31/12/2022   ZIMNAT LIFE ASSURANCE          376455           0.06   
1     06/05/2022               MASAWARA             5613           0.06   
2     31/12/2022                 Grandre          160000           0.06   
3     31/12/2022                 MINERVA           15000           0.08   
4     10/09/2022               ZAM-CARGO          364000           0.05   
5     05/04/2023  ZIMNAT LIFE ASSURANCE            30000           0.14   
6     31/12/2022               ZLA-Cargo          124575           0.10   
7     31/12/2022   ZIMNAT LION INSURANCE           50000           0.08   
8     31/12/2022   ZIMNAT LION INSURANCE           92800           0.06   
9     29/03/2023             BERAMASAMBA           30000           0.06   

   tenure                  repayment_frequency  frequency            method  
0      60                       Monthly (P+I)          12  reducing_balance  
1      60                       Monthly (P+I)          12  reducing_balance  
2      36               Quaterly (I+Bullet P)           4     straight_line  
3      36                        Bullet (P+I)           0     straight_line  
4      36      Annually(I) Principal rollover          12     straight_line  
5      24                       Monthly (P+I)          12  reducing_balance  
6      12      Annually(I) Principal rollover           1     straight_line  
7      12   Bi-annual(I)Principal at maturity           2     straight_line  
8      12   Bi-annual(I)Principal at maturity           2     straight_line  
9      12   Bi-annual(I)Principal at maturity           2     straight_line

In [38]:
long_term_borrowings_schedules = borrowings.calculate_borrowings_schedules(details_of_long_term_borrowings)
long_term_borrowings_schedules.keys()

dict_keys(['interest_payments', 'capital_repayments', 'outstanding_balance_at_start'])

In [39]:
details_of_short_term_borrowing

effective_date             institution  nominal_amount  interest_rate  \
0     24/04/2023                     FCB      120,383.84           0.18   
1     02/03/2023  ZIMNAT LIFE ASSURANCE        50,000.00           0.14   
2     31/12/2022   Zimnat Life Assurance       20,000.00           0.08   
3     31/12/2022                 Grandre      100,000.00           0.12   
4     23/04/2023                     FCB       18,429.93           1.50   
5     17/12/2022                 NURTURE      500,000.00           0.20   
6     26/01/2023                    NMB       450,000.00           0.18   
7     24/03/2023            DANDEMUTANDE       25,000.00           0.06   

   tenure               repayment_frequency  frequency            method  
0       3                     Bullet (P+I)           0     straight_line  
1       6                    Monthly (P+I)          12  reducing_balance  
2      12   Annually(I) Principal rollover           1     straight_line  
3      12            Quaterly (I+Bullet P)           4     straight_line  
4      12                     Bullet (P+I)           0     straight_line  
5      12            Quaterly (I+Bullet P)           4     straight_line  
6      12            Quaterly (I+Bullet P)           4     straight_line  
7      12                     Bullet (P+I)           0     straight_line

In [40]:
short_term_borrowings_schedules = borrowings.calculate_borrowings_schedules(details_of_short_term_borrowings)
short_term_borrowings_schedules.keys()

dict_keys(['interest_payments', 'capital_repayments', 'outstanding_balance_at_start'])

In [41]:
short_term_borrowings_schedules_outstanding_balances_df = (
    short_term_borrowings_schedules["outstanding_balance_at_start"]
)
short_term_borrowings_schedules_interest_payments_df = short_term_borrowings_schedules[
    "interest_payments"
]
short_term_borrowings_schedules_capital_repayments_df = short_term_borrowings_schedules[
    "capital_repayments"
]

In [42]:
long_term_borrowings_schedules_outstanding_balances_df = (
    long_term_borrowings_schedules["outstanding_balance_at_start"]
)
long_term_borrowings_schedules_interest_payments_df = long_term_borrowings_schedules[
    "interest_payments"
]
long_term_borrowings_schedules_capital_repayments_df = long_term_borrowings_schedules[
    "capital_repayments"
]

In [43]:
short_term_borrowings_schedules_interest_payments_df

Mar-2023  Apr-2023  May-2023  Jun-2023  Jul-2023  \
FCB                         0.00      0.00      0.00      0.00  5,417.27   
Zimnat Life Assurance       0.00      0.00      0.00      0.00      0.00   
Grandre                 3,000.00      0.00      0.00  3,000.00      0.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
NURTURE                25,000.00      0.00      0.00 25,000.00      0.00   
NMB                         0.00 20,250.00      0.00      0.00 20,250.00   
DANDEMUTANDE                0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00    548.94    459.93    369.94    278.97   

                        Aug-2023  Sep-2023  Oct-2023  Nov-2023  Dec-2023  \
FCB                         0.00      0.00      0.00       NaN      0.00   
Zimnat Life Assurance       0.00      0.00      0.00       NaN  1,600.00   
Grandre                     0.00  3,000.00      0.00       NaN  3,000.00   
FCB                         0.00      0.00      0.00       NaN      0.00   
NURTURE                     0.00 25,000.00      0.00       NaN 25,000.00   
NMB                         0.00      0.00 20,250.00       NaN      0.00   
DANDEMUTANDE                0.00      0.00      0.00       NaN      0.00   
ZIMNAT LIFE ASSURANCE     186.99     94.01      0.00       NaN      0.00   

                        Jan-2024  Feb-2024  Mar-2024  
FCB                         0.00       NaN      0.00  
Zimnat Life Assurance       0.00       NaN      0.00  
Grandre                     0.00       NaN      0.00  
FCB                         0.00       NaN      0.00  
NURTURE                     0.00       NaN      0.00  
NMB                    20,250.00       NaN      0.00  
DANDEMUTANDE                0.00       NaN  1,500.00  
ZIMNAT LIFE ASSURANCE       0.00       NaN      0.00

In [44]:
details_of_short_term_borrowing

effective_date             institution  nominal_amount  interest_rate  \
0     24/04/2023                     FCB      120,383.84           0.18   
1     02/03/2023  ZIMNAT LIFE ASSURANCE        50,000.00           0.14   
2     31/12/2022   Zimnat Life Assurance       20,000.00           0.08   
3     31/12/2022                 Grandre      100,000.00           0.12   
4     23/04/2023                     FCB       18,429.93           1.50   
5     17/12/2022                 NURTURE      500,000.00           0.20   
6     26/01/2023                    NMB       450,000.00           0.18   
7     24/03/2023            DANDEMUTANDE       25,000.00           0.06   

   tenure               repayment_frequency  frequency            method  
0       3                     Bullet (P+I)           0     straight_line  
1       6                    Monthly (P+I)          12  reducing_balance  
2      12   Annually(I) Principal rollover           1     straight_line  
3      12            Quaterly (I+Bullet P)           4     straight_line  
4      12                     Bullet (P+I)           0     straight_line  
5      12            Quaterly (I+Bullet P)           4     straight_line  
6      12            Quaterly (I+Bullet P)           4     straight_line  
7      12                     Bullet (P+I)           0     straight_line

In [45]:
capital_repayment_borrowings_df = pd.concat(
    [
        long_term_borrowings_schedules["capital_repayments"],
        short_term_borrowings_schedules["capital_repayments"],
    ],
    
).fillna(0)

capital_repayment_borrowings_df.loc['total'] = capital_repayment_borrowings_df.sum()

In [46]:
finance_costs_df = pd.concat(
    [
        long_term_borrowings_schedules["interest_payments"],
        short_term_borrowings_schedules["interest_payments"],
    ],
).fillna(0)

finance_costs_df.loc["total"] = finance_costs_df.sum()
finance_costs_df

Jun-2022  Jul-2022  Aug-2022  Sep-2022  Oct-2022  \
Grandre                     0.00      0.00      0.00      0.00      0.00   
MINERVA                     0.00      0.00      0.00      0.00      0.00   
ZAM-CARGO                   0.00      0.00      0.00      0.00  1,516.67   
ZLA-Cargo                   0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00      0.00      0.00   
BERAMASAMBA                 0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
MASAWARA                   27.32     26.93     26.53     26.14     25.74   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
Zimnat Life Assurance       0.00      0.00      0.00      0.00      0.00   
Grandre                     0.00      0.00      0.00      0.00      0.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
NURTURE                     0.00      0.00      0.00      0.00      0.00   
NMB                         0.00      0.00      0.00      0.00      0.00   
DANDEMUTANDE                0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
total                      27.32     26.93     26.53     26.14  1,542.40   

                        Nov-2022  Dec-2022  Jan-2023  Feb-2023  Mar-2023  \
Grandre                     0.00      0.00      0.00      0.00  2,400.00   
MINERVA                     0.00      0.00      0.00      0.00      0.00   
ZAM-CARGO               1,516.67  1,516.67  1,516.67  1,516.67  1,516.67   
ZLA-Cargo                   0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00      0.00      0.00   
BERAMASAMBA                 0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00      0.00  1,832.41  1,806.04  1,779.54   
MASAWARA                   25.34     24.93     24.53     24.12     23.71   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
Zimnat Life Assurance       0.00      0.00      0.00      0.00      0.00   
Grandre                     0.00      0.00      0.00      0.00  3,000.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
NURTURE                     0.00      0.00      0.00      0.00 25,000.00   
NMB                         0.00      0.00      0.00      0.00      0.00   
DANDEMUTANDE                0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
total                   1,542.00  1,541.60  3,373.61  3,346.83 33,719.92   

                        Apr-2023  May-2023  Jun-2023  Jul-2023  Aug-2023  \
Grandre                     0.00      0.00  2,400.00      0.00      0.00   
MINERVA                     0.00      0.00      0.00      0.00      0.00   
ZAM-CARGO               1,516.67  1,516.67  1,516.67  1,516.67  1,516.67   
ZLA-Cargo                   0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00  2,000.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00  2,784.00      0.00      0.00   
BERAMASAMBA                 0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE   1,752.91  1,726.16  1,699.27  1,672.25  1,645.10   
MASAWARA                   23.30     22.89     22.47     22.06     21.64   
ZIMNAT LIFE ASSURANCE       0.00    329.37    317.30    305.09    292.76   
FCB                         0.00      0.00      0.00  5,417.27      0.00   
Zimnat Life Assurance       0.00      0.00      0.00      0.00      0.

## **Income Statement**

In [47]:
income_statement_df = income_statement.generate_income_statement_template(
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)
income_statement_df

Sep-2023 Oct-2023 Nov-2023  \
INCOME_STATEMENT                                                          
Interest Income                                   NaN      NaN      NaN   
Other Income                                      NaN      NaN      NaN   
Total Revenue                                     NaN      NaN      NaN   
MANAGEMENT EXPENSES                               NaN      NaN      NaN   
STAFF COSTS                                       NaN      NaN      NaN   
Salaries                                          NaN      NaN      NaN   
Pensions & Statutory Contributions                NaN      NaN      NaN   
Training                                          NaN      NaN      NaN   
Bonus Provision                                   NaN      NaN      NaN   
Retrenchments                                     NaN      NaN      NaN   
Staff Welfare                                     NaN      NaN      NaN   
CILL                                              NaN      NaN      NaN   
Total Staff Costs                                 NaN      NaN      NaN   
TRAVEL & ENTERTAINMENT                            NaN      NaN      NaN   
Travel Costs                                      NaN      NaN      NaN   
Entertainment                                     NaN      NaN      NaN   
Total Travel & Entertainment                      NaN      NaN      NaN   
MARKETING AND PUBLIC RELATIONS                    NaN      NaN      NaN   
Marketing Costs                                   NaN      NaN      NaN   
Group Marketing Costs                             NaN      NaN      NaN   
Donations                                         NaN      NaN      NaN   
Total Marketing And Public Relations              NaN      NaN      NaN   
OFFICE COSTS                                      NaN      NaN      NaN   
Rental Costs                                      NaN      NaN      NaN   
Subscriptions                                     NaN      NaN      NaN   
Insurance                                         NaN      NaN      NaN   
Repairs And Maintenance                           NaN      NaN      NaN   
Utilities                                         NaN      NaN      NaN   
Stationery                                        NaN      NaN      NaN   
Admin Costs                                       NaN      NaN      NaN   
IT Costs                                          NaN      NaN      NaN   
Masawara Mgt Fee                                  NaN      NaN      NaN   
Fines And Penalties                               NaN      NaN      NaN   
Total Office Costs                                NaN      NaN      NaN   
PROFESSIONAL FEES                                 NaN      NaN      NaN   
Auditors Remuneration                             NaN      NaN      NaN   
Legal Fees                                        NaN      NaN      NaN   
Strategic Expenses                                NaN      NaN      NaN   
Directors Fees                                    NaN      NaN      NaN   
Consultancy Fees                                  NaN      NaN      NaN   
Total Professional Fees                           NaN      NaN      NaN   
COMMUNICATION COSTS                               NaN      NaN      NaN   
Telephones                                        NaN      NaN      NaN   
Cellphones                                        NaN      NaN      NaN   
Internet                                          NaN      NaN      NaN   
Courier                                           NaN      NaN      NaN   
Total Communication Costs                         NaN      NaN      NaN   
MOTOR VEHICLE COSTS                               NaN      NaN      NaN   
Fuel                                              NaN      NaN      NaN   
Motor Vehicle Maintenance Costs                   NaN      NaN      NaN   
Total Motor Vehicle Costs                         NaN      NaN      NaN   
OTHER COSTS                                       NaN      NaN      Na

### **Calculate Variable Expenses**

In [48]:
uncertain_expenses = expenses.calculate_uncertain_expenses(
    expenses_uncertain=expenses_uncertain,
    other_parameters=other_parameters,
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)
uncertain_expenses

Sep-2023  Oct-2023  Nov-2023  Dec-2023  Jan-2024  Feb-2024  Mar-2024  \
nothing      0.00      0.00      0.00      0.00      0.00      0.00      0.00   

         Apr-2024  May-2024  Jun-2024  Jul-2024  Aug-2024  Sep-2024  Oct-2024  \
nothing      0.00      0.00      0.00      0.00      0.00      0.00      0.00   

         Nov-2024  Dec-2024  Jan-2025  Feb-2025  Mar-2025  Apr-2025  May-2025  \
nothing      0.00      0.00      0.00      0.00      0.00      0.00      0.00   

         Jun-2025  Jul-2025  Aug-2025  Sep-2025  Oct-2025  Nov-2025  Dec-2025  \
nothing      0.00      0.00      0.00      0.00      0.00      0.00      0.00   

         Jan-2026  Feb-2026  Mar-2026  Apr-2026  May-2026  Jun-2026  Jul-2026  \
nothing      0.00      0.00      0.00      0.00      0.00      0.00      0.00   

         Aug-2026  Sep-2026  Oct-2026  Nov-2026  Dec-2026  Jan-2027  Feb-2027  \
nothing      0.00      0.00      0.00      0.00      0.00      0.00      0.00   

         Mar-2027  Apr-2027  May-2027  Jun-2027  Jul-2027  Aug-2027  Sep-2027  \
nothing      0.00      0.00      0.00      0.00      0.00      0.00      0.00   

         Oct-2027  Nov-2027  Dec-2027  Jan-2028  Feb-2028  Mar-2028  Apr-2028  \
nothing      0.00      0.00      0.00      0.00      0.00      0.00      0.00   

         May-2028  Jun-2028  Jul-2028  Aug-2028  
nothing      0.00      0.00      0.00      0.00

### **Calculate Change In Provision For Credit Loss**

In [49]:
change_in_provision_for_credit_loss = (
    expenses.calculate_change_in_provision_for_credit_loss(
        provision_for_credit_loss=provision_for_credit_loss_for_all_new_disbursements['total'],
        provision_for_credit_loss_opening_balances=float(
            opening_balances["PROVISION_FOR_CREDIT_LOSS"].iat[0]
        ),
        start_date=start_date, 
        months_to_forecast=months_to_forecast
    )
)

change_in_provision_for_credit_loss.head()

Sep-2023   7,320.00
Oct-2023     840.00
Nov-2023    -672.00
Dec-2023    -740.00
Jan-2024   2,375.60
Name: total, dtype: float64

### **Calculate Business Acquisition**

In [50]:
business_acquisition = expenses.calculate_business_acqusition(
    business_acquisition_percent=disbursement_parameters.loc['BUSINESS_ACQUISITION_PERCENT'],
    agent_contribution_percent=disbursement_parameters.loc['AGENT_CONTRIBUTION_PERCENT'],
    consumer_ssb_disbursements=new_disbursements_df['consumer_ssb_disbursements'],
    consumer_pvt_disbursements=new_disbursements_df['consumer_pvt_disbursements'],
)
business_acquisition.head()

Sep-2023   1,728.00
Oct-2023   2,160.00
Nov-2023   2,678.40
Dec-2023   3,048.00
Jan-2024   3,657.60
dtype: float64

### **Insert Revenue**

In [51]:
income_statement_df = income_statement.insert_revenue(
    income_statement=income_statement_df,
    interest_income=total_interest_income,
    other_income=other_income_df['total'],
)

income_statement_df

Sep-2023  Oct-2023   Nov-2023  \
INCOME_STATEMENT                                                              
Interest Income                               6,626.19 48,585.94  95,190.23   
Other Income                                 10,769.57 22,223.83  35,622.82   
Total Revenue                                17,395.76 70,809.77 130,813.05   
MANAGEMENT EXPENSES                                NaN       NaN        NaN   
STAFF COSTS                                        NaN       NaN        NaN   
Salaries                                           NaN       NaN        NaN   
Pensions & Statutory Contributions                 NaN       NaN        NaN   
Training                                           NaN       NaN        NaN   
Bonus Provision                                    NaN       NaN        NaN   
Retrenchments                                      NaN       NaN        NaN   
Staff Welfare                                      NaN       NaN        NaN   
CILL                                               NaN       NaN        NaN   
Total Staff Costs                                  NaN       NaN        NaN   
TRAVEL & ENTERTAINMENT                             NaN       NaN        NaN   
Travel Costs                                       NaN       NaN        NaN   
Entertainment                                      NaN       NaN        NaN   
Total Travel & Entertainment                       NaN       NaN        NaN   
MARKETING AND PUBLIC RELATIONS                     NaN       NaN        NaN   
Marketing Costs                                    NaN       NaN        NaN   
Group Marketing Costs                              NaN       NaN        NaN   
Donations                                          NaN       NaN        NaN   
Total Marketing And Public Relations               NaN       NaN        NaN   
OFFICE COSTS                                       NaN       NaN        NaN   
Rental Costs                                       NaN       NaN        NaN   
Subscriptions                                      NaN       NaN        NaN   
Insurance                                          NaN       NaN        NaN   
Repairs And Maintenance                            NaN       NaN        NaN   
Utilities                                          NaN       NaN        NaN   
Stationery                                         NaN       NaN        NaN   
Admin Costs                                        NaN       NaN        NaN   
IT Costs                                           NaN       NaN        NaN   
Masawara Mgt Fee                                   NaN       NaN        NaN   
Fines And Penalties                                NaN       NaN        NaN   
Total Office Costs                                 NaN       NaN        NaN   
PROFESSIONAL FEES                                  NaN       NaN        NaN   
Auditors Remuneration                              NaN       NaN        NaN   
Legal Fees                                         NaN       NaN        NaN   
Strategic Expenses                                 NaN       NaN        NaN   
Directors Fees                                     NaN       NaN        NaN   
Consultancy Fees                                   NaN       NaN        NaN   
Total Professional Fees                            NaN       NaN        NaN   
COMMUNICATION COSTS                                NaN       NaN        NaN   
Telephones                                         NaN       NaN        NaN   
Cellphones                                         NaN       NaN        NaN   
Internet                                           NaN       NaN        NaN   
Courier                                            NaN       NaN        NaN   
Total Communication Costs                          NaN       NaN        NaN   
MOTOR VEHICLE COSTS                                NaN       NaN        NaN   
Fuel                                               NaN       NaN        NaN   
Motor Vehicle Mai

### **Insert Static And Variable Inputs**

In [52]:
income_statement_df = income_statement.insert_expenses(
    income_statement=income_statement_df,
    expenses_certain=expenses_certain,
    uncertain_expenses=uncertain_expenses,
)

income_statement_df

Sep-2023  Oct-2023   Nov-2023  \
INCOME_STATEMENT                                                              
Interest Income                               6,626.19 48,585.94  95,190.23   
Other Income                                 10,769.57 22,223.83  35,622.82   
Total Revenue                                17,395.76 70,809.77 130,813.05   
MANAGEMENT EXPENSES                                NaN       NaN        NaN   
STAFF COSTS                                        NaN       NaN        NaN   
Salaries                                           NaN       NaN        NaN   
Pensions & Statutory Contributions                 NaN       NaN        NaN   
Training                                         40.00     40.00   6,840.00   
Bonus Provision                               2,023.00  2,023.00   2,023.00   
Retrenchments                                     0.00      0.00       0.00   
Staff Welfare                                17,275.00 17,275.00  17,275.00   
CILL                                              0.00      0.00       0.00   
Total Staff Costs                                  NaN       NaN        NaN   
TRAVEL & ENTERTAINMENT                             NaN       NaN        NaN   
Travel Costs                                      0.00      0.00   1,210.02   
Entertainment                                     0.00      0.00   1,210.02   
Total Travel & Entertainment                       NaN       NaN        NaN   
MARKETING AND PUBLIC RELATIONS                     NaN       NaN        NaN   
Marketing Costs                               4,850.00 19,450.00  27,950.00   
Group Marketing Costs                         5,922.33  5,922.33   5,922.33   
Donations                                         0.00      0.00       0.00   
Total Marketing And Public Relations               NaN       NaN        NaN   
OFFICE COSTS                                       NaN       NaN        NaN   
Rental Costs                                  1,257.94  1,257.94   1,257.94   
Subscriptions                                   265.06    265.06     265.06   
Insurance                                     2,666.67  2,666.67   2,666.67   
Repairs And Maintenance                         864.28    864.28     864.28   
Utilities                                     1,405.22  1,405.22   1,405.22   
Stationery                                      650.00    650.00     650.00   
Admin Costs                                  38,311.23 19,469.84  10,296.64   
IT Costs                                          0.00      0.00       0.00   
Masawara Mgt Fee                             11,766.15 11,766.15  11,766.15   
Fines And Penalties                               0.00      0.00       0.00   
Total Office Costs                                 NaN       NaN        NaN   
PROFESSIONAL FEES                                  NaN       NaN        NaN   
Auditors Remuneration                         1,875.00  1,630.43   1,388.89   
Legal Fees                                      200.00    200.00     200.00   
Strategic Expenses                                0.00      0.00       0.00   
Directors Fees                                  850.00    850.00     850.00   
Consultancy Fees                                  0.00      0.00   1,210.02   
Total Professional Fees                            NaN       NaN        NaN   
COMMUNICATION COSTS                                NaN       NaN        NaN   
Telephones                                      100.00    100.00     100.00   
Cellphones                                      214.00    214.00     214.00   
Internet                                      2,000.00  2,000.00   2,000.00   
Courier                                          85.00     85.00      85.00   
Total Communication Costs                          NaN       NaN        NaN   
MOTOR VEHICLE COSTS                                NaN       NaN        NaN   
Fuel                                          1,500.00  1,500.00   1,500.00   
Motor Vehicle Mai

### **Insert Salaries and Pensions And Statutory Contributions**

In [53]:
income_statement_df = income_statement.insert_salaries_and_pensions_and_statutory_contributions(
    income_statement=income_statement_df,
    salaries_and_pension_and_statutory_contributions_df=salaries_and_pension_and_statutory_contributions_df,
)

income_statement_df

Sep-2023  Oct-2023   Nov-2023  \
INCOME_STATEMENT                                                              
Interest Income                               6,626.19 48,585.94  95,190.23   
Other Income                                 10,769.57 22,223.83  35,622.82   
Total Revenue                                17,395.76 70,809.77 130,813.05   
MANAGEMENT EXPENSES                                NaN       NaN        NaN   
STAFF COSTS                                        NaN       NaN        NaN   
Salaries                                     31,400.00 33,440.00  37,160.00   
Pensions & Statutory Contributions            2,340.16  2,340.16   2,340.16   
Training                                         40.00     40.00   6,840.00   
Bonus Provision                               2,023.00  2,023.00   2,023.00   
Retrenchments                                     0.00      0.00       0.00   
Staff Welfare                                17,275.00 17,275.00  17,275.00   
CILL                                              0.00      0.00       0.00   
Total Staff Costs                                  NaN       NaN        NaN   
TRAVEL & ENTERTAINMENT                             NaN       NaN        NaN   
Travel Costs                                      0.00      0.00   1,210.02   
Entertainment                                     0.00      0.00   1,210.02   
Total Travel & Entertainment                       NaN       NaN        NaN   
MARKETING AND PUBLIC RELATIONS                     NaN       NaN        NaN   
Marketing Costs                               4,850.00 19,450.00  27,950.00   
Group Marketing Costs                         5,922.33  5,922.33   5,922.33   
Donations                                         0.00      0.00       0.00   
Total Marketing And Public Relations               NaN       NaN        NaN   
OFFICE COSTS                                       NaN       NaN        NaN   
Rental Costs                                  1,257.94  1,257.94   1,257.94   
Subscriptions                                   265.06    265.06     265.06   
Insurance                                     2,666.67  2,666.67   2,666.67   
Repairs And Maintenance                         864.28    864.28     864.28   
Utilities                                     1,405.22  1,405.22   1,405.22   
Stationery                                      650.00    650.00     650.00   
Admin Costs                                  38,311.23 19,469.84  10,296.64   
IT Costs                                          0.00      0.00       0.00   
Masawara Mgt Fee                             11,766.15 11,766.15  11,766.15   
Fines And Penalties                               0.00      0.00       0.00   
Total Office Costs                                 NaN       NaN        NaN   
PROFESSIONAL FEES                                  NaN       NaN        NaN   
Auditors Remuneration                         1,875.00  1,630.43   1,388.89   
Legal Fees                                      200.00    200.00     200.00   
Strategic Expenses                                0.00      0.00       0.00   
Directors Fees                                  850.00    850.00     850.00   
Consultancy Fees                                  0.00      0.00   1,210.02   
Total Professional Fees                            NaN       NaN        NaN   
COMMUNICATION COSTS                                NaN       NaN        NaN   
Telephones                                      100.00    100.00     100.00   
Cellphones                                      214.00    214.00     214.00   
Internet                                      2,000.00  2,000.00   2,000.00   
Courier                                          85.00     85.00      85.00   
Total Communication Costs                          NaN       NaN        NaN   
MOTOR VEHICLE COSTS                                NaN       NaN        NaN   
Fuel                                          1,500.00  1,500.00   1,500.00   
Motor Vehicle Mai

### **Insert Depreciation**

In [54]:
income_statement_df = income_statement.insert_depreciation(
    income_statement=income_statement_df,
    depreciation=depreciations_and_nbvs["dpns"]["total"],
)

### **Insert Change in Provision For Credit Loss**

In [55]:
income_statement_df = income_statement.insert_credit_loss_provision(
    income_statement=income_statement_df, 
    change_in_provision_for_credit_loss=change_in_provision_for_credit_loss,
)

In [56]:
provision_for_credit_loss = provision_for_credit_loss_for_all_new_disbursements["total"]
provision_for_credit_loss.head()

Sep-2023   7,320.00
Oct-2023   8,160.00
Nov-2023   7,488.00
Dec-2023   6,748.00
Jan-2024   9,123.60
Name: total, dtype: float64

### **Insert Business Acquisition**

In [57]:
income_statement_df = income_statement.insert_business_acquisition(
    income_statement=income_statement_df, business_acquisition=business_acquisition
)

### **Aggregations**

In [58]:
income_statement_df = income_statement.aggregate_staff_costs(income_statement_df)
income_statement_df = income_statement.aggregate_travel_and_entertainment(income_statement_df)
income_statement_df = income_statement.aggregate_marketing_and_public_relations(income_statement_df)
income_statement_df = income_statement.aggregate_office_costs(income_statement_df)
income_statement_df = income_statement.aggregate_professional_fees(income_statement_df)
income_statement_df = income_statement.aggregate_communication_costs(income_statement_df)
income_statement_df = income_statement.aggregate_motor_vehicle_costs(income_statement_df)
income_statement_df = income_statement.aggregate_other_costs(income_statement_df)
income_statement_df = income_statement.aggregate_investment_income(income_statement_df)
income_statement_df = income_statement.aggregate_finance_costs(income_statement_df)

### **Calculating Total Expenses and EBIDTA**

In [59]:
income_statement_df = income_statement.calculate_total_expenses(income_statement_df)
income_statement_df = income_statement.calculate_ebidta(income_statement_df)

### **Insert Finance Cost**

In [60]:
income_statement_df.loc["Finance Costs"] = finance_costs_df.loc["total"]
income_statement_df.loc["Finance Costs"] = income_statement_df.loc[
    "Finance Costs"
].fillna(0)
income_statement_df

Sep-2023   Oct-2023  \
INCOME_STATEMENT                                                      
Interest Income                                 6,626.19  48,585.94   
Other Income                                   10,769.57  22,223.83   
Total Revenue                                  17,395.76  70,809.77   
MANAGEMENT EXPENSES                                  NaN        NaN   
STAFF COSTS                                          NaN        NaN   
Salaries                                       31,400.00  33,440.00   
Pensions & Statutory Contributions              2,340.16   2,340.16   
Training                                           40.00      40.00   
Bonus Provision                                 2,023.00   2,023.00   
Retrenchments                                       0.00       0.00   
Staff Welfare                                  17,275.00  17,275.00   
CILL                                                0.00       0.00   
Total Staff Costs                              53,078.16  55,118.16   
TRAVEL & ENTERTAINMENT                               NaN        NaN   
Travel Costs                                        0.00       0.00   
Entertainment                                       0.00       0.00   
Total Travel & Entertainment                        0.00       0.00   
MARKETING AND PUBLIC RELATIONS                       NaN        NaN   
Marketing Costs                                 4,850.00  19,450.00   
Group Marketing Costs                           5,922.33   5,922.33   
Donations                                           0.00       0.00   
Total Marketing And Public Relations           10,772.33  25,372.33   
OFFICE COSTS                                         NaN        NaN   
Rental Costs                                    1,257.94   1,257.94   
Subscriptions                                     265.06     265.06   
Insurance                                       2,666.67   2,666.67   
Repairs And Maintenance                           864.28     864.28   
Utilities                                       1,405.22   1,405.22   
Stationery                                        650.00     650.00   
Admin Costs                                    38,311.23  19,469.84   
IT Costs                                            0.00       0.00   
Masawara Mgt Fee                               11,766.15  11,766.15   
Fines And Penalties                                 0.00       0.00   
Total Office Costs                             57,186.55  38,345.16   
PROFESSIONAL FEES                                    NaN        NaN   
Auditors Remuneration                           1,875.00   1,630.43   
Legal Fees                                        200.00     200.00   
Strategic Expenses                                  0.00       0.00   
Directors Fees                                    850.00     850.00   
Consultancy Fees                                    0.00       0.00   
Total Professional Fees                         2,925.00   2,680.43   
COMMUNICATION COSTS                                  NaN        NaN   
Telephones                                        100.00     100.00   
Cellphones                                        214.00     214.00   
Internet                                        2,000.00   2,000.00   
Courier                                            85.00      85.00   
Total Communication Costs                       2,399.00   2,399.00   
MOTOR VEHICLE COSTS                                  NaN        NaN   
Fuel                                            1,500.00   1,500.00   
Motor Vehicle Maintenance Costs                 1,000.00   1,000.00   
Total Motor Vehicle Costs                       2,500.00   2,500.00   
OTHER COSTS                                          NaN        NaN   
Depreciation                                    8,187.46   8,187.46   
Bank Charges                                    9,226.69   9,226.69   
Zimnat Grp Shared Costs Recovery Exp                0.00       0.00   
P

### **Aggregate Finance Cost**

In [61]:
income_statement_df = income_statement.aggregate_finance_costs(income_statement_df)

### **Calculate Profit Before Tax**

In [62]:
income_statement_df = income_statement.calculate_profit_before_tax(income_statement_df)

### **Calculate Tax**

In [63]:
income_statement_df = income_statement.calculate_tax(
    income_statement=income_statement_df, tax_rate=other_parameters.loc["TAX_RATE"]
)
income_statement_df

Sep-2023   Oct-2023  \
INCOME_STATEMENT                                                      
Interest Income                                 6,626.19  48,585.94   
Other Income                                   10,769.57  22,223.83   
Total Revenue                                  17,395.76  70,809.77   
MANAGEMENT EXPENSES                                  NaN        NaN   
STAFF COSTS                                          NaN        NaN   
Salaries                                       31,400.00  33,440.00   
Pensions & Statutory Contributions              2,340.16   2,340.16   
Training                                           40.00      40.00   
Bonus Provision                                 2,023.00   2,023.00   
Retrenchments                                       0.00       0.00   
Staff Welfare                                  17,275.00  17,275.00   
CILL                                                0.00       0.00   
Total Staff Costs                              53,078.16  55,118.16   
TRAVEL & ENTERTAINMENT                               NaN        NaN   
Travel Costs                                        0.00       0.00   
Entertainment                                       0.00       0.00   
Total Travel & Entertainment                        0.00       0.00   
MARKETING AND PUBLIC RELATIONS                       NaN        NaN   
Marketing Costs                                 4,850.00  19,450.00   
Group Marketing Costs                           5,922.33   5,922.33   
Donations                                           0.00       0.00   
Total Marketing And Public Relations           10,772.33  25,372.33   
OFFICE COSTS                                         NaN        NaN   
Rental Costs                                    1,257.94   1,257.94   
Subscriptions                                     265.06     265.06   
Insurance                                       2,666.67   2,666.67   
Repairs And Maintenance                           864.28     864.28   
Utilities                                       1,405.22   1,405.22   
Stationery                                        650.00     650.00   
Admin Costs                                    38,311.23  19,469.84   
IT Costs                                            0.00       0.00   
Masawara Mgt Fee                               11,766.15  11,766.15   
Fines And Penalties                                 0.00       0.00   
Total Office Costs                             57,186.55  38,345.16   
PROFESSIONAL FEES                                    NaN        NaN   
Auditors Remuneration                           1,875.00   1,630.43   
Legal Fees                                        200.00     200.00   
Strategic Expenses                                  0.00       0.00   
Directors Fees                                    850.00     850.00   
Consultancy Fees                                    0.00       0.00   
Total Professional Fees                         2,925.00   2,680.43   
COMMUNICATION COSTS                                  NaN        NaN   
Telephones                                        100.00     100.00   
Cellphones                                        214.00     214.00   
Internet                                        2,000.00   2,000.00   
Courier                                            85.00      85.00   
Total Communication Costs                       2,399.00   2,399.00   
MOTOR VEHICLE COSTS                                  NaN        NaN   
Fuel                                            1,500.00   1,500.00   
Motor Vehicle Maintenance Costs                 1,000.00   1,000.00   
Total Motor Vehicle Costs                       2,500.00   2,500.00   
OTHER COSTS                                          NaN        NaN   
Depreciation                                    8,187.46   8,187.46   
Bank Charges                                    9,226.69   9,226.69   
Zimnat Grp Shared Costs Recovery Exp                0.00       0.00   
P

## **Direct Cashflow**

In [64]:
direct_cashflow_df = direct_cashflow.generate_direct_cashflow_template(
    start_date=start_date, months_to_forecast=months_to_forecast
)

direct_cashflow_df

Sep-2023  Oct-2023  \
DIRECT_CASHFLOW_STATEMENT                                                
CASH INFLOWS                                             NaN       NaN   
Short Term Borrowing                                     NaN       NaN   
Long Term Borrowing                                      NaN       NaN   
Capital Repayment                                        NaN       NaN   
Interest Income                                          NaN       NaN   
Other Income                                             NaN       NaN   
Receipts From Receivables                                NaN       NaN   
Sale Of Other Assets                                     NaN       NaN   
Issue Of Equity And Intercompany Loans                   NaN       NaN   
Total Cash Inflows                                       NaN       NaN   
CASH OUTFLOWS                                            NaN       NaN   
Disbursements                                            NaN       NaN   
Interest Expense                                         NaN       NaN   
Capital Repayment On Borrowings                          NaN       NaN   
Operating Expenses                                       NaN       NaN   
Capital Expenses                                         NaN       NaN   
Payments To Payables                                     NaN       NaN   
Repayments On Intercompany Loans and Equity Buy...       NaN       NaN   
Purchase Of Inventory                                    NaN       NaN   
Purchase Of Other Assets                                 NaN       NaN   
Dividend Paid                                            NaN       NaN   
Tax Paid                                                 NaN       NaN   
Total Cash Outflows                                      NaN       NaN   
Net Increase/Decrease In Cash                            NaN       NaN   
Opening Balance                                          NaN       NaN   
Closing Balance                                          NaN       NaN   

                                                    Nov-2023  Dec-2023  \
DIRECT_CASHFLOW_STATEMENT                                                
CASH INFLOWS                                             NaN       NaN   
Short Term Borrowing                                     NaN       NaN   
Long Term Borrowing                                      NaN       NaN   
Capital Repayment                                        NaN       NaN   
Interest Income                                          NaN       NaN   
Other Income                                             NaN       NaN   
Receipts From Receivables                                NaN       NaN   
Sale Of Other Assets                                     NaN       NaN   
Issue Of Equity And Intercompany Loans                   NaN       NaN   
Total Cash Inflows                                       NaN       NaN   
CASH OUTFLOWS                                            NaN       NaN   
Disbursements                                            NaN       NaN   
Interest Expense                                         NaN       NaN   
Capital Repayment On Borrowings                          NaN       NaN   
Operating Expenses                                       NaN       NaN   
Capital Expenses                                         NaN       NaN   
Payments To Payables                                     NaN       NaN   
Repayments On Intercompany Loans and Equity Buy...       NaN       NaN   
Purchase Of Inventory                                    NaN       NaN   
Purchase Of Other Assets                                 NaN       NaN   
Dividend Paid                                            NaN       NaN   
Tax Paid                                                 NaN       NaN   
Total Cash Outflows                                      NaN       NaN   
Net Increase/Decrease In Cash                            NaN       NaN   
Opening Balance                                        

### **Insert Available Direct Cashflow Items**

#### **From Parameters**

In [65]:
direct_cashflow_df.loc[
    "Receipts From Receivables"
] = helper.change_period_index_to_strftime(
    helper.add_series(
        [
            other_parameters.loc["RECEIPTS_FROM_OTHER_RECEIVABLES"],
            other_parameters.loc["RECEIPTS_FROM_TRADE_RECEIVABLES"],
            other_parameters.loc["RECEIPTS_FROM_INTERGROUP_RECEIVABLES"],
        ]
    )
)

direct_cashflow_df.loc[
    "Purchase Of Inventory"
] = helper.change_period_index_to_strftime(other_parameters.loc["NEW_INVENTORY"])
direct_cashflow_df.loc[
    "Payments To Payables"
] = -helper.change_period_index_to_strftime(
    helper.add_series(
        [
            other_parameters.loc["PAYMENTS_TO_TRADE_PAYABLES"],
            other_parameters.loc["PAYMENTS_TO_OTHER_PAYABLES"],
        ]
    )
)

direct_cashflow_df.loc["Dividend Paid"] = -helper.change_period_index_to_strftime(
    other_parameters.loc["DIVIDEND_PAID"]
)

#### **From Calculations/Income Statement**

In [66]:
direct_cashflow_df.loc['Interest Income'] = income_statement_df.loc['Interest Income']
direct_cashflow_df.loc['Other Income'] = income_statement_df.loc['Other Income']
direct_cashflow_df.loc['Interest Expense'] = -income_statement_df.loc['Finance Costs']
direct_cashflow_df.loc['Disbursements'] = -helper.change_period_index_to_strftime(new_disbursements_df['total'])

In [67]:
direct_cashflow_df

Sep-2023    Oct-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                       NaN         NaN   
Long Term Borrowing                                        NaN         NaN   
Capital Repayment                                          NaN         NaN   
Interest Income                                       6,626.19   48,585.94   
Other Income                                         10,769.57   22,223.83   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                       NaN         NaN   
Issue Of Equity And Intercompany Loans                     NaN         NaN   
Total Cash Inflows                                         NaN         NaN   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -609,011.05 -651,480.25   
Interest Expense                                    -34,829.99  -23,645.54   
Capital Repayment On Borrowings                            NaN         NaN   
Operating Expenses                                         NaN         NaN   
Capital Expenses                                           NaN         NaN   
Payments To Payables                                     -0.00  -13,404.72   
Repayments On Intercompany Loans and Equity Buy...         NaN         NaN   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                   NaN         NaN   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                   NaN         NaN   
Total Cash Outflows                                        NaN         NaN   
Net Increase/Decrease In Cash                              NaN         NaN   
Opening Balance                                            NaN         NaN   
Closing Balance                                            NaN         NaN   

                                                      Nov-2023    Dec-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                       NaN         NaN   
Long Term Borrowing                                        NaN         NaN   
Capital Repayment                                          NaN         NaN   
Interest Income                                      95,190.23  145,937.14   
Other Income                                         35,622.82   47,628.35   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                       NaN         NaN   
Issue Of Equity And Intercompany Loans                     NaN         NaN   
Total Cash Inflows                                         NaN         NaN   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -805,080.25 -808,900.00   
Interest Expense                                     -3,354.82  -52,555.32   
Capital Repayment On Borrowings                            NaN         NaN   
Operating Expenses                                         NaN         NaN   
Capital Expenses                                           NaN         NaN   
Payments To Payables                                -68,786.66  -80,963.15   
Repayments On Intercompany Loans and Equity Buy...         NaN         NaN   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                   NaN         NaN   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                   NaN         NaN 

### **Equity and Intercompany Loans**

In [68]:
direct_cashflow_df = direct_cashflow.add_equity_and_intercompany_loans(
    other_parameters=other_parameters, direct_cashflow_df=direct_cashflow_df
)

### **Other Assets**


In [69]:
direct_cashflow_df = direct_cashflow.add_other_assets(
    other_parameters=other_parameters, direct_cashflow_df=direct_cashflow_df
)

### **Tax Paid**

In [70]:
tax_schedule = direct_cashflow.generate_tax_schedule(
    taxation=income_statement_df.loc["Taxation"],
    opening_balance=opening_balances["DEFERED_TAXATION"].iat[0],
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)

tax_schedule

Sep-2023 Oct-2023 Nov-2023  Dec-2023  Jan-2024  Feb-2024  \
Opening Balance        0     0.00     0.00      0.00      0.00 23,195.78   
Tax Charged            0        0        0  4,875.68 23,195.78 40,602.37   
Tax Paid           -0.00    -0.00    -0.00 -4,875.68     -0.00     -0.00   
Closing Balance     0.00     0.00     0.00      0.00 23,195.78 63,798.15   

                   Mar-2024  Apr-2024   May-2024    Jun-2024   Jul-2024  \
Opening Balance   63,798.15      0.00  71,576.17  158,530.96       0.00   
Tax Charged       56,340.04 71,576.17  86,954.79  112,460.85 139,268.35   
Tax Paid        -120,138.19     -0.00      -0.00 -270,991.82      -0.00   
Closing Balance        0.00 71,576.17 158,530.96        0.00 139,268.35   

                  Aug-2024    Sep-2024   Oct-2024   Nov-2024    Dec-2024  \
Opening Balance 139,268.35  300,035.07       0.00 193,049.92  396,949.17   
Tax Charged     160,766.72  177,800.71 193,049.92 203,899.25  212,143.77   
Tax Paid             -0.00 -477,835.78      -0.00      -0.00 -609,092.94   
Closing Balance 300,035.07        0.00 193,049.92 396,949.17        0.00   

                  Jan-2025   Feb-2025    Mar-2025   Apr-2025   May-2025  \
Opening Balance       0.00 218,700.59  440,368.58       0.00 224,978.14   
Tax Charged     218,700.59 221,667.99  224,172.98 224,978.14 224,096.30   
Tax Paid             -0.00      -0.00 -664,541.56      -0.00      -0.00   
Closing Balance 218,700.59 440,368.58        0.00 224,978.14 449,074.44   

                   Jun-2025   Jul-2025   Aug-2025    Sep-2025   Oct-2025  \
Opening Balance  449,074.44       0.00 224,986.29  448,861.16       0.00   
Tax Charged      224,428.24 224,986.29 223,874.86  224,278.39 225,228.26   
Tax Paid        -673,502.68      -0.00      -0.00 -673,139.54      -0.00   
Closing Balance        0.00 224,986.29 448,861.16        0.00 225,228.26   

                  Nov-2025    Dec-2025   Jan-2026   Feb-2026    Mar-2026  \
Opening Balance 225,228.26  449,460.28       0.00 225,163.25  449,238.56   
Tax Charged     224,232.02  223,691.31 225,163.25 224,075.31  225,040.00   
Tax Paid             -0.00 -673,151.59      -0.00      -0.00 -674,278.56   
Closing Balance 449,460.28        0.00 225,163.25 449,238.56        0.00   

                  Apr-2026   May-2026    Jun-2026   Jul-2026   Aug-2026  \
Opening Balance       0.00 225,010.38  448,999.92       0.00 224,932.77   
Tax Charged     225,010.38 223,989.54  224,962.56 224,932.77 223,809.65   
Tax Paid             -0.00      -0.00 -673,962.48      -0.00      -0.00   
Closing Balance 225,010.38 448,999.92        0.00 224,932.77 448,742.43   

                   Sep-2026   Oct-2026   Nov-2026    Dec-2026   Jan-2027  \
Opening Balance  448,742.43       0.00 224,761.72  448,477.19       0.00   
Tax Charged      224,788.41 224,761.72 223,715.47  224,701.64 224,671.53   
Tax Paid        -673,530.84      -0.00      -0.00 -673,178.83      -0.00   
Closing Balance        0.00 224,761.72 448,477.19        0.00 224,671.53   

                  Feb-2027    Mar-2027   Apr-2027   May-2027    Jun-2027  \
Opening Balance 224,671.53  448,230.51       0.00 224,551.30  448,078.51   
Tax Charged     223,558.98  224,555.01 224,551.30 223,527.21  224,534.10   
Tax Paid             -0.00 -672,785.52      -0.00      -0.00 -672,612.61   
Closing Balance 448,230.51        0.00 224,551.30 448,078.51        0.00   

                  Jul-2027   Aug-2027    Sep-2027   Oct-2027   Nov-2027  \
Opening Balance       0.00 224,586.44  448,000.62       0.00 224,495.52   
Tax Charged     224,586.44 223,414.19  224,422.82 224,495.52 223,427.28   
Tax Paid             -0.00      -0.00 -672,423.44      -0.00      -0.00   
Closing Balance 224,586.44 448,000.62        0.00 224,495.52 447,922.80   

                   Dec-2027   Jan-2028   Feb-2028    Mar-2028   Apr-2028  \
Opening Balance  447,922.80       0.00 224,418.60  447,691.40       0.00   
Tax Charged      224,452.34 224,418.60 223,272.80  224,287.91 224,253.85  

In [71]:
direct_cashflow_df.loc['Tax Paid'] = tax_schedule.loc['Tax Paid']

### **Calculate Operating Expenses**

In [72]:
operating_expenses = direct_cashflow.calculate_operating_expenses(income_statement=income_statement_df)
operating_expenses.head()

Sep-2023   137,792.72
Oct-2023   135,778.77
Nov-2023   149,532.48
Dec-2023   133,427.24
Jan-2024   130,870.15
dtype: object

### **Insert Operating Expenses**

In [73]:
direct_cashflow_df.loc['Operating Expenses']  = -operating_expenses
direct_cashflow_df


Sep-2023    Oct-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                       NaN         NaN   
Long Term Borrowing                                        NaN         NaN   
Capital Repayment                                          NaN         NaN   
Interest Income                                       6,626.19   48,585.94   
Other Income                                         10,769.57   22,223.83   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                      0.00        0.00   
Issue Of Equity And Intercompany Loans                    0.00        0.00   
Total Cash Inflows                                         NaN         NaN   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -609,011.05 -651,480.25   
Interest Expense                                    -34,829.99  -23,645.54   
Capital Repayment On Borrowings                            NaN         NaN   
Operating Expenses                                 -137,792.72 -135,778.77   
Capital Expenses                                           NaN         NaN   
Payments To Payables                                     -0.00  -13,404.72   
Repayments On Intercompany Loans and Equity Buy...       -0.00      933.88   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                  0.00        0.00   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                 -0.00       -0.00   
Total Cash Outflows                                        NaN         NaN   
Net Increase/Decrease In Cash                              NaN         NaN   
Opening Balance                                            NaN         NaN   
Closing Balance                                            NaN         NaN   

                                                      Nov-2023    Dec-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                       NaN         NaN   
Long Term Borrowing                                        NaN         NaN   
Capital Repayment                                          NaN         NaN   
Interest Income                                      95,190.23  145,937.14   
Other Income                                         35,622.82   47,628.35   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                      0.00        0.00   
Issue Of Equity And Intercompany Loans                    0.00        0.00   
Total Cash Inflows                                         NaN         NaN   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -805,080.25 -808,900.00   
Interest Expense                                     -3,354.82  -52,555.32   
Capital Repayment On Borrowings                            NaN         NaN   
Operating Expenses                                 -149,532.48 -133,427.24   
Capital Expenses                                           NaN         NaN   
Payments To Payables                                -68,786.66  -80,963.15   
Repayments On Intercompany Loans and Equity Buy...      922.36    1,091.91   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                  0.00        0.00   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                 -0.00   -4,875.68 

### **Calculate Capital Expenses**

In [74]:
capital_expenses = direct_cashflow.calculate_capital_expenses(
    details_of_assets=details_of_assets,
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)

capital_expenses.head()

Sep-2023        0
Oct-2023        0
Nov-2023        0
Dec-2023        0
Jan-2024    41540
Name: book_value, dtype: int64

### **Insert Capital Expenses**

In [75]:
direct_cashflow_df.loc['Capital Expenses'] = -capital_expenses

### **Calculate Direct Cashflow Borrowings**

In [76]:
long_and_short_term_borrowing_df = (
    direct_cashflow.calculate_long_and_short_term_borrowing_for_direct_cashflow(
        details_of_long_term_borrowing=details_of_long_term_borrowing,
        details_of_short_term_borrowing=details_of_short_term_borrowing,
        start_date=start_date,
        months_to_forecast=months_to_forecast,
    )
)

long_and_short_term_borrowing_df

long_term_borrowing  short_term_borrowing  total
Sep-2023                    0                  0.00   0.00
Oct-2023                    0                  0.00   0.00
Nov-2023                    0                  0.00   0.00
Dec-2023                    0                  0.00   0.00
Jan-2024                    0                  0.00   0.00
Feb-2024                    0                  0.00   0.00
Mar-2024                    0                  0.00   0.00
Apr-2024                    0                  0.00   0.00
May-2024                    0                  0.00   0.00
Jun-2024                    0                  0.00   0.00
Jul-2024                    0                  0.00   0.00
Aug-2024                    0                  0.00   0.00
Sep-2024                    0                  0.00   0.00
Oct-2024                    0                  0.00   0.00
Nov-2024                    0                  0.00   0.00
Dec-2024                    0                  0.00   0.00
Jan-2025                    0                  0.00   0.00
Feb-2025                    0                  0.00   0.00
Mar-2025                    0                  0.00   0.00
Apr-2025                    0                  0.00   0.00
May-2025                    0                  0.00   0.00
Jun-2025                    0                  0.00   0.00
Jul-2025                    0                  0.00   0.00
Aug-2025                    0                  0.00   0.00
Sep-2025                    0                  0.00   0.00
Oct-2025                    0                  0.00   0.00
Nov-2025                    0                  0.00   0.00
Dec-2025                    0                  0.00   0.00
Jan-2026                    0                  0.00   0.00
Feb-2026                    0                  0.00   0.00
Mar-2026                    0                  0.00   0.00
Apr-2026                    0                  0.00   0.00
May-2026                    0                  0.00   0.00
Jun-2026                    0                  0.00   0.00
Jul-2026                    0                  0.00   0.00
Aug-2026                    0                  0.00   0.00
Sep-2026                    0                  0.00   0.00
Oct-2026                    0                  0.00   0.00
Nov-2026                    0                  0.00   0.00
Dec-2026                    0                  0.00   0.00
Jan-2027                    0                  0.00   0.00
Feb-2027                    0                  0.00   0.00
Mar-2027                    0                  0.00   0.00
Apr-2027                    0                  0.00   0.00
May-2027                    0                  0.00   0.00
Jun-2027                    0                  0.00   0.00
Jul-2027                    0                  0.00   0.00
Aug-2027                    0                  0.00   0.00
Sep-2027                    0                  0.00   0.00
Oct-2027                    0                  0.00   0.00
Nov-2027                    0                  0.00   0.00
Dec-2027                    0                  0.00   0.00
Jan-2028                    0                  0.00   0.00
Feb-2028                    0                  0.00   0.00
Mar-2028                    0                  0.00   0.00
Apr-2028                    0                  0.00   0.00
May-2028                    0                  0.00   0.00
Jun-2028                    0                  0.00   0.00
Jul-2028                    0                  0.00   0.00
Aug-2028                    0                  0.00   0.00

### **Insert Direct Cashflow Borrowing**

In [77]:
direct_cashflow_df.loc['Short Term Borrowing'] = long_and_short_term_borrowing_df['short_term_borrowing']
direct_cashflow_df.loc['Long Term Borrowing'] = long_and_short_term_borrowing_df['long_term_borrowing']

In [78]:
direct_cashflow_df

Sep-2023    Oct-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                      0.00        0.00   
Long Term Borrowing                                       0.00        0.00   
Capital Repayment                                          NaN         NaN   
Interest Income                                       6,626.19   48,585.94   
Other Income                                         10,769.57   22,223.83   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                      0.00        0.00   
Issue Of Equity And Intercompany Loans                    0.00        0.00   
Total Cash Inflows                                         NaN         NaN   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -609,011.05 -651,480.25   
Interest Expense                                    -34,829.99  -23,645.54   
Capital Repayment On Borrowings                            NaN         NaN   
Operating Expenses                                 -137,792.72 -135,778.77   
Capital Expenses                                          0.00        0.00   
Payments To Payables                                     -0.00  -13,404.72   
Repayments On Intercompany Loans and Equity Buy...       -0.00      933.88   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                  0.00        0.00   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                 -0.00       -0.00   
Total Cash Outflows                                        NaN         NaN   
Net Increase/Decrease In Cash                              NaN         NaN   
Opening Balance                                            NaN         NaN   
Closing Balance                                            NaN         NaN   

                                                      Nov-2023    Dec-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                      0.00        0.00   
Long Term Borrowing                                       0.00        0.00   
Capital Repayment                                          NaN         NaN   
Interest Income                                      95,190.23  145,937.14   
Other Income                                         35,622.82   47,628.35   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                      0.00        0.00   
Issue Of Equity And Intercompany Loans                    0.00        0.00   
Total Cash Inflows                                         NaN         NaN   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -805,080.25 -808,900.00   
Interest Expense                                     -3,354.82  -52,555.32   
Capital Repayment On Borrowings                            NaN         NaN   
Operating Expenses                                 -149,532.48 -133,427.24   
Capital Expenses                                          0.00        0.00   
Payments To Payables                                -68,786.66  -80,963.15   
Repayments On Intercompany Loans and Equity Buy...      922.36    1,091.91   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                  0.00        0.00   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                 -0.00   -4,875.68 

### **Calculate Capital Repayments**

In [79]:
capital_repayment = helper.add_series(
[existing_loans_schedules['capital_repayments'].sum()
    , capital_repayment_new_disbursements_df['total']]
)

capital_repayment.loc[helper.generate_columns(start_date,months_to_forecast)].head()

Sep-2023    59,655.62
Oct-2023    74,039.92
Nov-2023   143,135.17
Dec-2023   231,424.90
Jan-2024   320,985.26
dtype: float64

### **Insert Capital Repayment**

In [80]:
direct_cashflow_df.loc['Capital Repayment'] = capital_repayment

### **Calculate Capital Repayments on Borrowings**


In [81]:
capital_repayment_borrowings_df

Jun-2022  Jul-2022  Aug-2022  Sep-2022  Oct-2022  \
Grandre                     0.00      0.00      0.00      0.00      0.00   
MINERVA                     0.00      0.00      0.00      0.00      0.00   
ZAM-CARGO                   0.00      0.00      0.00      0.00      0.00   
ZLA-Cargo                   0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00      0.00      0.00   
BERAMASAMBA                 0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
MASAWARA                   80.78     81.17     81.57     81.96     82.36   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
Zimnat Life Assurance       0.00      0.00      0.00      0.00      0.00   
Grandre                     0.00      0.00      0.00      0.00      0.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
NURTURE                     0.00      0.00      0.00      0.00      0.00   
NMB                         0.00      0.00      0.00      0.00      0.00   
DANDEMUTANDE                0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
total                      80.78     81.17     81.57     81.96     82.36   

                        Nov-2022  Dec-2022  Jan-2023  Feb-2023  Mar-2023  \
Grandre                     0.00      0.00      0.00      0.00      0.00   
MINERVA                     0.00      0.00      0.00      0.00      0.00   
ZAM-CARGO                   0.00      0.00      0.00      0.00      0.00   
ZLA-Cargo                   0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00      0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00      0.00      0.00   
BERAMASAMBA                 0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00      0.00  5,417.73  5,444.10  5,470.60   
MASAWARA                   82.76     83.17     83.57     83.98     84.39   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
Zimnat Life Assurance       0.00      0.00      0.00      0.00      0.00   
Grandre                     0.00      0.00      0.00      0.00      0.00   
FCB                         0.00      0.00      0.00      0.00      0.00   
NURTURE                     0.00      0.00      0.00      0.00      0.00   
NMB                         0.00      0.00      0.00      0.00      0.00   
DANDEMUTANDE                0.00      0.00      0.00      0.00      0.00   
ZIMNAT LIFE ASSURANCE       0.00      0.00      0.00      0.00      0.00   
total                      82.76     83.17  5,501.30  5,528.08  5,554.98   

                        Apr-2023  May-2023  Jun-2023   Jul-2023  Aug-2023  \
Grandre                     0.00      0.00      0.00       0.00      0.00   
MINERVA                     0.00      0.00      0.00       0.00      0.00   
ZAM-CARGO                   0.00      0.00      0.00       0.00      0.00   
ZLA-Cargo                   0.00      0.00      0.00       0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00       0.00      0.00   
ZIMNAT LION INSURANCE       0.00      0.00      0.00       0.00      0.00   
BERAMASAMBA                 0.00      0.00      0.00       0.00      0.00   
ZIMNAT LIFE ASSURANCE   5,497.23  5,523.98  5,550.87   5,577.89  5,605.04   
MASAWARA                   84.80     85.21     85.63      86.04     86.46   
ZIMNAT LIFE ASSURANCE       0.00  1,099.35  1,111.42   1,123.62  1,135.96   
FCB                         0.00      0.00      0.00 120,383.84      0.00   
Zimnat Life Assurance       0.00      0.00      0.00      

### **Insert Capital Repayment on New Borrowings**

In [82]:
direct_cashflow_df.loc[
    "Capital Repayment On Borrowings"
] = -capital_repayment_borrowings_df.loc["total"]

direct_cashflow_df.loc["Capital Repayment On Borrowings"] = direct_cashflow_df.loc[
    "Capital Repayment On Borrowings"
].fillna(0)

### **Calculate Direct Cashflow Totals**

In [83]:
direct_cashflow_df

Sep-2023    Oct-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                      0.00        0.00   
Long Term Borrowing                                       0.00        0.00   
Capital Repayment                                    59,655.62   74,039.92   
Interest Income                                       6,626.19   48,585.94   
Other Income                                         10,769.57   22,223.83   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                      0.00        0.00   
Issue Of Equity And Intercompany Loans                    0.00        0.00   
Total Cash Inflows                                         NaN         NaN   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -609,011.05 -651,480.25   
Interest Expense                                    -34,829.99  -23,645.54   
Capital Repayment On Borrowings                     -15,430.09   -6,908.08   
Operating Expenses                                 -137,792.72 -135,778.77   
Capital Expenses                                          0.00        0.00   
Payments To Payables                                     -0.00  -13,404.72   
Repayments On Intercompany Loans and Equity Buy...       -0.00      933.88   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                  0.00        0.00   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                 -0.00       -0.00   
Total Cash Outflows                                        NaN         NaN   
Net Increase/Decrease In Cash                              NaN         NaN   
Opening Balance                                            NaN         NaN   
Closing Balance                                            NaN         NaN   

                                                      Nov-2023    Dec-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                      0.00        0.00   
Long Term Borrowing                                       0.00        0.00   
Capital Repayment                                   143,135.17  231,424.90   
Interest Income                                      95,190.23  145,937.14   
Other Income                                         35,622.82   47,628.35   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                      0.00        0.00   
Issue Of Equity And Intercompany Loans                    0.00        0.00   
Total Cash Inflows                                         NaN         NaN   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -805,080.25 -808,900.00   
Interest Expense                                     -3,354.82  -52,555.32   
Capital Repayment On Borrowings                      -6,948.81 -894,364.80   
Operating Expenses                                 -149,532.48 -133,427.24   
Capital Expenses                                          0.00        0.00   
Payments To Payables                                -68,786.66  -80,963.15   
Repayments On Intercompany Loans and Equity Buy...      922.36    1,091.91   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                  0.00        0.00   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                 -0.00   -4,875.68 

In [84]:
direct_cashflow_df.loc["Total Cash Inflows"] = direct_cashflow_df.iloc[
    direct_cashflow_df.index.get_loc("CASH INFLOWS")
    + 1 : direct_cashflow_df.index.get_loc("Total Cash Inflows")
].sum()


direct_cashflow_df.loc["Total Cash Outflows"] = direct_cashflow_df.iloc[
    direct_cashflow_df.index.get_loc("CASH OUTFLOWS")
    + 1 : direct_cashflow_df.index.get_loc("Total Cash Outflows")
].sum()

direct_cashflow_df.loc["Net Increase/Decrease In Cash"] = (
    direct_cashflow_df.loc["Total Cash Inflows"]
    + direct_cashflow_df.loc["Total Cash Outflows"]
)

### **Calculate Opening and Closing Balances**

In [85]:
depreciations_and_nbvs['dpns'].sum(axis = 1).head()

Sep-2023   16,374.93
Oct-2023   16,374.93
Nov-2023   15,375.03
Dec-2023   15,375.03
Jan-2024   15,083.79
dtype: float64

In [86]:
depreciations_and_nbvs['nbvs'].sum(axis = 1).head()

Sep-2023   1,071,584.87
Oct-2023   1,055,209.94
Nov-2023   1,039,834.92
Dec-2023   1,024,459.89
Jan-2024   1,009,667.35
dtype: float64

In [87]:
direct_cashflow_df

Sep-2023    Oct-2023  \
DIRECT_CASHFLOW_STATEMENT                                                    
CASH INFLOWS                                               NaN         NaN   
Short Term Borrowing                                      0.00        0.00   
Long Term Borrowing                                       0.00        0.00   
Capital Repayment                                    59,655.62   74,039.92   
Interest Income                                       6,626.19   48,585.94   
Other Income                                         10,769.57   22,223.83   
Receipts From Receivables                                 0.00        0.00   
Sale Of Other Assets                                      0.00        0.00   
Issue Of Equity And Intercompany Loans                    0.00        0.00   
Total Cash Inflows                                   77,051.38  144,849.69   
CASH OUTFLOWS                                              NaN         NaN   
Disbursements                                      -609,011.05 -651,480.25   
Interest Expense                                    -34,829.99  -23,645.54   
Capital Repayment On Borrowings                     -15,430.09   -6,908.08   
Operating Expenses                                 -137,792.72 -135,778.77   
Capital Expenses                                          0.00        0.00   
Payments To Payables                                     -0.00  -13,404.72   
Repayments On Intercompany Loans and Equity Buy...       -0.00      933.88   
Purchase Of Inventory                                     0.00        0.00   
Purchase Of Other Assets                                  0.00        0.00   
Dividend Paid                                            -0.00       -0.00   
Tax Paid                                                 -0.00       -0.00   
Total Cash Outflows                                -797,063.86 -830,283.47   
Net Increase/Decrease In Cash                      -720,012.48 -685,433.78   
Opening Balance                                            NaN         NaN   
Closing Balance                                            NaN         NaN   

                                                        Nov-2023  \
DIRECT_CASHFLOW_STATEMENT                                          
CASH INFLOWS                                                 NaN   
Short Term Borrowing                                        0.00   
Long Term Borrowing                                         0.00   
Capital Repayment                                     143,135.17   
Interest Income                                        95,190.23   
Other Income                                           35,622.82   
Receipts From Receivables                                   0.00   
Sale Of Other Assets                                        0.00   
Issue Of Equity And Intercompany Loans                      0.00   
Total Cash Inflows                                    273,948.22   
CASH OUTFLOWS                                                NaN   
Disbursements                                        -805,080.25   
Interest Expense                                       -3,354.82   
Capital Repayment On Borrowings                        -6,948.81   
Operating Expenses                                   -149,532.48   
Capital Expenses                                            0.00   
Payments To Payables                                  -68,786.66   
Repayments On Intercompany Loans and Equity Buy...        922.36   
Purchase Of Inventory                                       0.00   
Purchase Of Other Assets                                    0.00   
Dividend Paid                                              -0.00   
Tax Paid                                                   -0.00   
Total Cash Outflows                                -1,032,780.66   
Net Increase/Decrease In Cash                        -758,832.44   
Opening Balance                                              NaN   
Closing Balance                  

In [88]:
tax_schedule

Sep-2023 Oct-2023 Nov-2023  Dec-2023  Jan-2024  Feb-2024  \
Opening Balance        0     0.00     0.00      0.00      0.00 23,195.78   
Tax Charged            0        0        0  4,875.68 23,195.78 40,602.37   
Tax Paid           -0.00    -0.00    -0.00 -4,875.68     -0.00     -0.00   
Closing Balance     0.00     0.00     0.00      0.00 23,195.78 63,798.15   

                   Mar-2024  Apr-2024   May-2024    Jun-2024   Jul-2024  \
Opening Balance   63,798.15      0.00  71,576.17  158,530.96       0.00   
Tax Charged       56,340.04 71,576.17  86,954.79  112,460.85 139,268.35   
Tax Paid        -120,138.19     -0.00      -0.00 -270,991.82      -0.00   
Closing Balance        0.00 71,576.17 158,530.96        0.00 139,268.35   

                  Aug-2024    Sep-2024   Oct-2024   Nov-2024    Dec-2024  \
Opening Balance 139,268.35  300,035.07       0.00 193,049.92  396,949.17   
Tax Charged     160,766.72  177,800.71 193,049.92 203,899.25  212,143.77   
Tax Paid             -0.00 -477,835.78      -0.00      -0.00 -609,092.94   
Closing Balance 300,035.07        0.00 193,049.92 396,949.17        0.00   

                  Jan-2025   Feb-2025    Mar-2025   Apr-2025   May-2025  \
Opening Balance       0.00 218,700.59  440,368.58       0.00 224,978.14   
Tax Charged     218,700.59 221,667.99  224,172.98 224,978.14 224,096.30   
Tax Paid             -0.00      -0.00 -664,541.56      -0.00      -0.00   
Closing Balance 218,700.59 440,368.58        0.00 224,978.14 449,074.44   

                   Jun-2025   Jul-2025   Aug-2025    Sep-2025   Oct-2025  \
Opening Balance  449,074.44       0.00 224,986.29  448,861.16       0.00   
Tax Charged      224,428.24 224,986.29 223,874.86  224,278.39 225,228.26   
Tax Paid        -673,502.68      -0.00      -0.00 -673,139.54      -0.00   
Closing Balance        0.00 224,986.29 448,861.16        0.00 225,228.26   

                  Nov-2025    Dec-2025   Jan-2026   Feb-2026    Mar-2026  \
Opening Balance 225,228.26  449,460.28       0.00 225,163.25  449,238.56   
Tax Charged     224,232.02  223,691.31 225,163.25 224,075.31  225,040.00   
Tax Paid             -0.00 -673,151.59      -0.00      -0.00 -674,278.56   
Closing Balance 449,460.28        0.00 225,163.25 449,238.56        0.00   

                  Apr-2026   May-2026    Jun-2026   Jul-2026   Aug-2026  \
Opening Balance       0.00 225,010.38  448,999.92       0.00 224,932.77   
Tax Charged     225,010.38 223,989.54  224,962.56 224,932.77 223,809.65   
Tax Paid             -0.00      -0.00 -673,962.48      -0.00      -0.00   
Closing Balance 225,010.38 448,999.92        0.00 224,932.77 448,742.43   

                   Sep-2026   Oct-2026   Nov-2026    Dec-2026   Jan-2027  \
Opening Balance  448,742.43       0.00 224,761.72  448,477.19       0.00   
Tax Charged      224,788.41 224,761.72 223,715.47  224,701.64 224,671.53   
Tax Paid        -673,530.84      -0.00      -0.00 -673,178.83      -0.00   
Closing Balance        0.00 224,761.72 448,477.19        0.00 224,671.53   

                  Feb-2027    Mar-2027   Apr-2027   May-2027    Jun-2027  \
Opening Balance 224,671.53  448,230.51       0.00 224,551.30  448,078.51   
Tax Charged     223,558.98  224,555.01 224,551.30 223,527.21  224,534.10   
Tax Paid             -0.00 -672,785.52      -0.00      -0.00 -672,612.61   
Closing Balance 448,230.51        0.00 224,551.30 448,078.51        0.00   

                  Jul-2027   Aug-2027    Sep-2027   Oct-2027   Nov-2027  \
Opening Balance       0.00 224,586.44  448,000.62       0.00 224,495.52   
Tax Charged     224,586.44 223,414.19  224,422.82 224,495.52 223,427.28   
Tax Paid             -0.00      -0.00 -672,423.44      -0.00      -0.00   
Closing Balance 224,586.44 448,000.62        0.00 224,495.52 447,922.80   

                   Dec-2027   Jan-2028   Feb-2028    Mar-2028   Apr-2028  \
Opening Balance  447,922.80       0.00 224,418.60  447,691.40       0.00   
Tax Charged      224,452.34 224,418.60 223,272.80  224,287.91 224,253.85  

In [89]:
direct_cashflow_df= direct_cashflow.calculate_opening_and_closing_balances_for_direct_cashflows(
direct_cashflow=direct_cashflow_df, 
cash_on_hand_opening_balance= opening_balances['CASH_ON_HAND'].iat[0]
)

direct_cashflow_df

Sep-2023      Oct-2023  \
DIRECT_CASHFLOW_STATEMENT                                                      
CASH INFLOWS                                               NaN           NaN   
Short Term Borrowing                                      0.00          0.00   
Long Term Borrowing                                       0.00          0.00   
Capital Repayment                                    59,655.62     74,039.92   
Interest Income                                       6,626.19     48,585.94   
Other Income                                         10,769.57     22,223.83   
Receipts From Receivables                                 0.00          0.00   
Sale Of Other Assets                                      0.00          0.00   
Issue Of Equity And Intercompany Loans                    0.00          0.00   
Total Cash Inflows                                   77,051.38    144,849.69   
CASH OUTFLOWS                                              NaN           NaN   
Disbursements                                      -609,011.05   -651,480.25   
Interest Expense                                    -34,829.99    -23,645.54   
Capital Repayment On Borrowings                     -15,430.09     -6,908.08   
Operating Expenses                                 -137,792.72   -135,778.77   
Capital Expenses                                          0.00          0.00   
Payments To Payables                                     -0.00    -13,404.72   
Repayments On Intercompany Loans and Equity Buy...       -0.00        933.88   
Purchase Of Inventory                                     0.00          0.00   
Purchase Of Other Assets                                  0.00          0.00   
Dividend Paid                                            -0.00         -0.00   
Tax Paid                                                 -0.00         -0.00   
Total Cash Outflows                                -797,063.86   -830,283.47   
Net Increase/Decrease In Cash                      -720,012.48   -685,433.78   
Opening Balance                                     331,856.00   -388,156.48   
Closing Balance                                    -388,156.48 -1,073,590.26   

                                                        Nov-2023  \
DIRECT_CASHFLOW_STATEMENT                                          
CASH INFLOWS                                                 NaN   
Short Term Borrowing                                        0.00   
Long Term Borrowing                                         0.00   
Capital Repayment                                     143,135.17   
Interest Income                                        95,190.23   
Other Income                                           35,622.82   
Receipts From Receivables                                   0.00   
Sale Of Other Assets                                        0.00   
Issue Of Equity And Intercompany Loans                      0.00   
Total Cash Inflows                                    273,948.22   
CASH OUTFLOWS                                                NaN   
Disbursements                                        -805,080.25   
Interest Expense                                       -3,354.82   
Capital Repayment On Borrowings                        -6,948.81   
Operating Expenses                                   -149,532.48   
Capital Expenses                                            0.00   
Payments To Payables                                  -68,786.66   
Repayments On Intercompany Loans and Equity Buy...        922.36   
Purchase Of Inventory                                       0.00   
Purchase Of Other Assets                                    0.00   
Dividend Paid                                              -0.00   
Tax Paid                                                   -0.00   
Total Cash Outflows                                -1,032,780.66   
Net Increase/Decrease In Cash                        -758,832.44   
Opening Balance                              

In [90]:
direct_cashflow_yearly_df = direct_cashflow.calculate_direct_cashflow_yearly(
    direct_cashflow_df = direct_cashflow_df, opening_balances = opening_balances
)
direct_cashflow_yearly_df

2023  \
DIRECT_CASHFLOW_STATEMENT                                          
CASH INFLOWS                                                0.00   
Short Term Borrowing                                        0.00   
Long Term Borrowing                                         0.00   
Capital Repayment                                     508,255.61   
Interest Income                                       296,339.50   
Other Income                                          116,244.57   
Receipts From Receivables                                   0.00   
Sale Of Other Assets                                        0.00   
Issue Of Equity And Intercompany Loans                      0.00   
Total Cash Inflows                                    920,839.68   
CASH OUTFLOWS                                               0.00   
Disbursements                                      -2,874,471.55   
Interest Expense                                     -114,385.67   
Capital Repayment On Borrowings                      -923,651.79   
Operating Expenses                                   -556,531.21   
Capital Expenses                                            0.00   
Payments To Payables                                 -163,154.52   
Repayments On Intercompany Loans and Equity Buy...      2,948.15   
Purchase Of Inventory                                       0.00   
Purchase Of Other Assets                                    0.00   
Dividend Paid                                               0.00   
Tax Paid                                               -4,875.68   
Total Cash Outflows                                -4,634,122.28   
Net Increase/Decrease In Cash                      -3,713,282.59   
Opening Balance                                       331,856.00   
Closing Balance                                    -3,381,426.59   

                                                             2024  \
DIRECT_CASHFLOW_STATEMENT                                           
CASH INFLOWS                                                 0.00   
Short Term Borrowing                                         0.00   
Long Term Borrowing                                          0.00   
Capital Repayment                                   11,659,056.64   
Interest Income                                      5,990,310.02   
Other Income                                         1,933,297.90   
Receipts From Receivables                            1,187,638.92   
Sale Of Other Assets                                         0.00   
Issue Of Equity And Intercompany Loans                     935.69   
Total Cash Inflows                                  20,771,239.16   
CASH OUTFLOWS                                                0.00   
Disbursements                                      -21,264,812.25   
Interest Expense                                       -68,714.53   
Capital Repayment On Borrowings                       -592,178.96   
Operating Expenses                                  -1,999,066.18   
Capital Expenses                                      -338,730.00   
Payments To Payables                                  -466,687.36   
Repayments On Intercompany Loans and Equity Buy...       3,468.14   
Purchase Of Inventory                                        0.00   
Purchase Of Other Assets                                     0.00   
Dividend Paid                                                0.00   
Tax Paid                                            -1,478,058.72   
Total Cash Outflows                                -26,204,779.87   
Net Increase/Decrease In Cash                       -5,433,540.71   
Opening Balance                                     -3,381,426.59   
Closing Balance                                     -8,814,967.30   

                                                             2025  \
DIRECT_CASHFLOW_STATEMENT                                           
CASH INFLOWS                                                 0.00   
Short Term Borr

### **Calculate IMTT (2% Tax)**

In [91]:
income_statement_df.loc['2% Taxation']  = -direct_cashflow_df.loc['Total Cash Outflows']*imtt

## **Calculate Profit and Loss for the Period**


In [92]:
income_statement_df = income_statement.calculate_profit_or_loss_for_period(income_statement_df)
income_statement_df

Sep-2023   Oct-2023  \
INCOME_STATEMENT                                                      
Interest Income                                 6,626.19  48,585.94   
Other Income                                   10,769.57  22,223.83   
Total Revenue                                  17,395.76  70,809.77   
MANAGEMENT EXPENSES                                  NaN        NaN   
STAFF COSTS                                          NaN        NaN   
Salaries                                       31,400.00  33,440.00   
Pensions & Statutory Contributions              2,340.16   2,340.16   
Training                                           40.00      40.00   
Bonus Provision                                 2,023.00   2,023.00   
Retrenchments                                       0.00       0.00   
Staff Welfare                                  17,275.00  17,275.00   
CILL                                                0.00       0.00   
Total Staff Costs                              53,078.16  55,118.16   
TRAVEL & ENTERTAINMENT                               NaN        NaN   
Travel Costs                                        0.00       0.00   
Entertainment                                       0.00       0.00   
Total Travel & Entertainment                        0.00       0.00   
MARKETING AND PUBLIC RELATIONS                       NaN        NaN   
Marketing Costs                                 4,850.00  19,450.00   
Group Marketing Costs                           5,922.33   5,922.33   
Donations                                           0.00       0.00   
Total Marketing And Public Relations           10,772.33  25,372.33   
OFFICE COSTS                                         NaN        NaN   
Rental Costs                                    1,257.94   1,257.94   
Subscriptions                                     265.06     265.06   
Insurance                                       2,666.67   2,666.67   
Repairs And Maintenance                           864.28     864.28   
Utilities                                       1,405.22   1,405.22   
Stationery                                        650.00     650.00   
Admin Costs                                    38,311.23  19,469.84   
IT Costs                                            0.00       0.00   
Masawara Mgt Fee                               11,766.15  11,766.15   
Fines And Penalties                                 0.00       0.00   
Total Office Costs                             57,186.55  38,345.16   
PROFESSIONAL FEES                                    NaN        NaN   
Auditors Remuneration                           1,875.00   1,630.43   
Legal Fees                                        200.00     200.00   
Strategic Expenses                                  0.00       0.00   
Directors Fees                                    850.00     850.00   
Consultancy Fees                                    0.00       0.00   
Total Professional Fees                         2,925.00   2,680.43   
COMMUNICATION COSTS                                  NaN        NaN   
Telephones                                        100.00     100.00   
Cellphones                                        214.00     214.00   
Internet                                        2,000.00   2,000.00   
Courier                                            85.00      85.00   
Total Communication Costs                       2,399.00   2,399.00   
MOTOR VEHICLE COSTS                                  NaN        NaN   
Fuel                                            1,500.00   1,500.00   
Motor Vehicle Maintenance Costs                 1,000.00   1,000.00   
Total Motor Vehicle Costs                       2,500.00   2,500.00   
OTHER COSTS                                          NaN        NaN   
Depreciation                                    8,187.46   8,187.46   
Bank Charges                                    9,226.69   9,226.69   
Zimnat Grp Shared Costs Recovery Exp                0.00       0.00   
P

## **Loan Book**

In [93]:
loan_book_df = loan_book.generate_loan_book_template(
    start_date=start_date, months_to_forecast=months_to_forecast
)
loan_book_df

Sep-2023 Oct-2023 Nov-2023 Dec-2023 Jan-2024 Feb-2024  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN      NaN      NaN      NaN      NaN   

                  Mar-2024 Apr-2024 May-2024 Jun-2024 Jul-2024 Aug-2024  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN      NaN      NaN      NaN      NaN   

                  Sep-2024 Oct-2024 Nov-2024 Dec-2024 Jan-2025 Feb-2025  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN      NaN      NaN      NaN      NaN   

                  Mar-2025 Apr-2025 May-2025 Jun-2025 Jul-2025 Aug-2025  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN      NaN      NaN      NaN      NaN   

                  Sep-2025 Oct-2025 Nov-2025 Dec-2025 Jan-2026 Feb-2026  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN      NaN      NaN      NaN      NaN   

                  Mar-2026 Apr-2026 May-2026 Jun-2026 Jul-2026 Aug-2026  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN      NaN      NaN      NaN      NaN   

                  Sep-2026 Oct-2026 Nov-2026 Dec-2026 Jan-2027 Feb-2027  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN      NaN      NaN      NaN      NaN   

                  Mar-2027 Apr-2027 May-2027 Jun-2027 Jul-2027 Aug-2027  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN      NaN      NaN      NaN      NaN   

                  Sep-2027 Oct-2027 Nov-2027 Dec-2027 Jan-2028 Feb-2028  \
Opening Balance        NaN      NaN      NaN      NaN      NaN      NaN   
New Disbursements      NaN      NaN      NaN      NaN      NaN      NaN   
Repayments             NaN      NaN      NaN      NaN      NaN      NaN   
Interest Income        NaN      NaN      NaN      NaN      NaN      NaN   
Closing Balance        NaN      NaN

### **Insert Loan Book Items**

In [94]:
capital_repayment_existing_loans = existing_loans_schedules['capital_repayments'].sum()
capital_repayment_existing_loans.loc[helper.generate_columns(start_date,12)]

Sep-2023   59,655.62
Oct-2023   10,092.45
Nov-2023    6,747.14
Dec-2023    4,764.47
Jan-2024    2,982.53
Feb-2024    2,973.78
Mar-2024    2,659.76
Apr-2024    2,630.20
May-2024    1,473.53
Jun-2024    1,477.22
Jul-2024    1,480.91
Aug-2024    1,484.61
dtype: float64

In [95]:
total_capital_repayments = loan_book.aggregate_new_and_existing_loans_capital_repayments(
    capital_repayments_new_disbursements_df = capital_repayment_new_disbursements_df,
    capital_repayments_existing_loans = capital_repayment_existing_loans,
    start_date = start_date,
    months_to_forecast = months_to_forecast,
)

total_capital_repayments.head()

Sep-2023    59,655.62
Oct-2023    74,039.92
Nov-2023   143,135.17
Dec-2023   231,424.90
Jan-2024   320,985.26
dtype: float64

In [96]:

loan_book_df = loan_book.insert_loan_book_items(
    loan_book=loan_book_df,
    opening_balance_on_loan_book=existing_loans_schedules_outstanding_balances_df.sum()[
        pd.Timestamp(start_date).strftime("%b-%Y")
    ],
    total_interest_income=total_interest_income,
    total_capital_repayments=total_capital_repayments,
    disbursements=helper.change_period_index_to_strftime(new_disbursements_df["total"]),
)

loan_book_df

Sep-2023    Oct-2023    Nov-2023    Dec-2023     Jan-2024  \
Opening Balance   112,077.25         NaN         NaN         NaN          NaN   
New Disbursements 609,011.05  651,480.25  805,080.25  808,900.00 1,097,573.00   
Repayments        -66,281.81 -122,625.86 -238,325.40 -377,362.04  -505,716.43   
Interest Income     6,626.19   48,585.94   95,190.23  145,937.14   184,731.17   
Closing Balance          NaN         NaN         NaN         NaN          NaN   

                      Feb-2024     Mar-2024      Apr-2024      May-2024  \
Opening Balance            NaN          NaN           NaN           NaN   
New Disbursements 1,141,909.25 1,396,650.00  1,588,680.00  1,735,000.00   
Repayments         -687,691.18  -876,063.25 -1,010,695.04 -1,179,441.17   
Interest Income     237,068.35   283,231.12    336,267.28    401,711.37   
Closing Balance            NaN          NaN           NaN           NaN   

                       Jun-2024      Jul-2024      Aug-2024      Sep-2024  \
Opening Balance             NaN           NaN           NaN           NaN   
New Disbursements  2,095,000.00  2,035,000.00  2,035,000.00  2,035,000.00   
Repayments        -1,350,484.40 -1,598,698.22 -1,790,355.38 -1,968,088.96   
Interest Income      461,740.95    545,824.65    614,979.59    672,213.45   
Closing Balance             NaN           NaN           NaN           NaN   

                       Oct-2024      Nov-2024      Dec-2024      Jan-2025  \
Opening Balance             NaN           NaN           NaN           NaN   
New Disbursements  2,035,000.00  2,035,000.00  2,035,000.00  2,035,000.00   
Repayments        -2,123,707.26 -2,230,235.79 -2,328,189.57 -2,415,286.54   
Interest Income      717,951.75    753,170.12    781,420.21    802,536.84   
Closing Balance             NaN           NaN           NaN           NaN   

                       Feb-2025      Mar-2025      Apr-2025      May-2025  \
Opening Balance             NaN           NaN           NaN           NaN   
New Disbursements  2,035,000.00  2,035,000.00  2,035,000.00  2,035,000.00   
Repayments        -2,500,159.16 -2,587,691.27 -2,593,846.02 -2,594,047.49   
Interest Income      817,641.67    826,199.02    827,612.28    828,113.67   
Closing Balance             NaN           NaN           NaN           NaN   

                       Jun-2025      Jul-2025      Aug-2025      Sep-2025  \
Opening Balance             NaN           NaN           NaN           NaN   
New Disbursements  2,035,000.00  2,035,000.00  2,035,000.00  2,035,000.00   
Repayments        -2,594,047.49 -2,594,047.49 -2,593,106.65 -2,593,106.65   
Interest Income      828,111.34    828,109.00    828,106.65    828,106.65   
Closing Balance             NaN           NaN           NaN           NaN   

                       Oct-2025      Nov-2025      Dec-2025      Jan-2026  \
Opening Balance             NaN           NaN           NaN           NaN   
New Disbursements  2,035,000.00  2,035,000.00  2,035,000.00  2,035,000.00   
Repayments        -2,593,106.65 -2,593,106.65 -2,593,106.65 -2,593,106.65   
Interest Income      828,106.65    828,106.65    828,106.65    828,106.65   
Closing Balance             NaN           NaN           NaN           NaN   

                       Feb-2026      Mar-2026      Apr-2026      May-2026  \
Opening Balance             NaN           NaN           NaN           NaN   
New Disbursements  2,035,000.00  2,035,000.00  2,035,000.00  2,035,000.00   
Repayments        -2,593,106.65 -2,593,106.65 -2,593,106.65 -2,593,106.65   
Interest Income      828,106.65    828,106.65    828,106.65    828,106.65   
Closing Balance             NaN           NaN           NaN           NaN   

                       Jun-2026      Jul-2026      Aug-2026      Sep-2026  \
Opening Balance             NaN           NaN           NaN           NaN   
New Disbursements  2,035,000.00  2,035,000.00  2,035,000.00  2,035,000.00   
Repayments        -2,593,106.65 -2,593,106.65 -2,593,106.65 -2,593,106.65

### **Calculate Opening and Closing Balances for Loan Book**

In [97]:
loan_book_df = helper.calculate_opening_and_closing_balances(loan_book_df)
loan_book_df.to_csv("loan_book_df.csv")

In [98]:
loan_book_yearly_df = loan_book.calculate_loan_book_yearly(loan_book=loan_book_df)
loan_book_yearly_df

2023           2024           2025           2026  \
Opening Balance   3,913,201.01   6,279,416.95  15,885,172.56  19,359,370.94   
New Disbursements 2,874,471.55  21,264,812.25  24,420,000.00  24,420,000.00   
Repayments         -804,595.11 -17,649,366.65 -30,844,658.70 -31,117,279.81   
Interest Income     296,339.50   5,990,310.02   9,898,857.07   9,937,279.81   
Closing Balance   6,279,416.95  15,885,172.56  19,359,370.94  22,599,370.94   

                            2027           2028  
Opening Balance    22,599,370.94  25,839,370.94  
New Disbursements  24,420,000.00  16,280,000.00  
Repayments        -31,117,279.81 -20,744,853.21  
Interest Income     9,937,279.81   6,624,853.21  
Closing Balance    25,839,370.94  27,999,370.94

## **Balance Sheet**


In [99]:
balance_sheet_df = balance_sheet.generate_balance_sheet_template(
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)

balance_sheet_df

Sep-2023 Oct-2023 Nov-2023 Dec-2023  \
STATEMENT_OF_FINANCIAL_POSITION                                           
ASSETS                                   NaN      NaN      NaN      NaN   
NON CURRENT ASSETS                       NaN      NaN      NaN      NaN   
Property Plant And Equipment             NaN      NaN      NaN      NaN   
Intangible Assets                        NaN      NaN      NaN      NaN   
Investment In Subsidiaries               NaN      NaN      NaN      NaN   
Investment In Associates                 NaN      NaN      NaN      NaN   
Investment Properties                    NaN      NaN      NaN      NaN   
Equity Investments                       NaN      NaN      NaN      NaN   
Long Term Money Market Investments       NaN      NaN      NaN      NaN   
Loans To Related Entities                NaN      NaN      NaN      NaN   
Non Current Assets                       NaN      NaN      NaN      NaN   
CURRENT ASSETS                           NaN      NaN      NaN      NaN   
Inventories                              NaN      NaN      NaN      NaN   
Intergroup Receivables                   NaN      NaN      NaN      NaN   
Loan Book                                NaN      NaN      NaN      NaN   
Trade Receivables                        NaN      NaN      NaN      NaN   
Other Receivables                        NaN      NaN      NaN      NaN   
Cash On Hand                             NaN      NaN      NaN      NaN   
Short Term Money Market Investments      NaN      NaN      NaN      NaN   
Current Assets                           NaN      NaN      NaN      NaN   
TOTAL ASSETS                             NaN      NaN      NaN      NaN   
EQUITY AND LIABILITIES                   NaN      NaN      NaN      NaN   
CAPITAL AND RESERVES                     NaN      NaN      NaN      NaN   
Issued Share Capital                     NaN      NaN      NaN      NaN   
Share Premium                            NaN      NaN      NaN      NaN   
Other Components Of Equity               NaN      NaN      NaN      NaN   
Treasury Shares                          NaN      NaN      NaN      NaN   
Retained Earnings                        NaN      NaN      NaN      NaN   
Capital And Reserves                     NaN      NaN      NaN      NaN   
NON CURRENT LIABILITIES                  NaN      NaN      NaN      NaN   
Loans                                    NaN      NaN      NaN      NaN   
Intercompany Loans                       NaN      NaN      NaN      NaN   
Deferred Taxation                        NaN      NaN      NaN      NaN   
Non Current Liabilities                  NaN      NaN      NaN      NaN   
CURRENT LIABILITIES                      NaN      NaN      NaN      NaN   
Trade Payables                           NaN      NaN      NaN      NaN   
Other Payables                           NaN      NaN      NaN      NaN   
Borrowings                               NaN      NaN      NaN      NaN   
Provision For Taxation                   NaN      NaN      NaN      NaN   
Provisions                               NaN      NaN      NaN      NaN   
Current Liabilities                      NaN      NaN      NaN      NaN   
TOTAL EQUITY AND LIABILITIES             NaN      NaN      NaN      NaN   
CHECK                                    NaN      NaN      NaN      NaN   

                                    Jan-2024 Feb-2024 Mar-2024 Apr-2024  \
STATEMENT_OF_FINANCIAL_POSITION                                           
ASSETS                                   NaN      NaN      NaN      NaN   
NON CURRENT ASSETS                       NaN      NaN      NaN      NaN   
Property Plant And Equipment             NaN      NaN      NaN      NaN   
Intangible Assets                        NaN      NaN      NaN      NaN   
Investment In Subsidiaries               NaN      NaN      NaN      NaN   
Investment In Associates                 NaN      NaN      NaN      NaN   
Investment Properties                    NaN      NaN      N

### **Insert Available Balance Sheet Items**

In [100]:
depreciations_and_nbvs.keys()

dict_keys(['nbvs', 'dpns'])

In [101]:
balance_sheet_df.loc["Property Plant And Equipment"] = depreciations_and_nbvs["nbvs"][
    "total"
]

balance_sheet_df.loc["Loan Book"] = loan_book_df.loc["Closing Balance"]

balance_sheet_df.loc["Cash On Hand"] = direct_cashflow_df.loc["Closing Balance"]

balance_sheet_df.loc[
    "Provisions"
] = provision_for_credit_loss_for_all_new_disbursements["total"]


balance_sheet_df.loc["Provision For Taxation"] = helper.change_period_index_to_strftime(
    other_parameters.loc["PROVISION_FOR_TAX"]
)

balance_sheet_df

Sep-2023      Oct-2023      Nov-2023  \
STATEMENT_OF_FINANCIAL_POSITION                                               
ASSETS                                      NaN           NaN           NaN   
NON CURRENT ASSETS                          NaN           NaN           NaN   
Property Plant And Equipment         535,792.44    527,604.97    519,917.46   
Intangible Assets                           NaN           NaN           NaN   
Investment In Subsidiaries                  NaN           NaN           NaN   
Investment In Associates                    NaN           NaN           NaN   
Investment Properties                       NaN           NaN           NaN   
Equity Investments                          NaN           NaN           NaN   
Long Term Money Market Investments          NaN           NaN           NaN   
Loans To Related Entities                   NaN           NaN           NaN   
Non Current Assets                          NaN           NaN           NaN   
CURRENT ASSETS                              NaN           NaN           NaN   
Inventories                                 NaN           NaN           NaN   
Intergroup Receivables                      NaN           NaN           NaN   
Loan Book                            661,432.67  1,238,873.01  1,900,818.08   
Trade Receivables                           NaN           NaN           NaN   
Other Receivables                           NaN           NaN           NaN   
Cash On Hand                        -388,156.48 -1,073,590.26 -1,832,422.70   
Short Term Money Market Investments         NaN           NaN           NaN   
Current Assets                              NaN           NaN           NaN   
TOTAL ASSETS                                NaN           NaN           NaN   
EQUITY AND LIABILITIES                      NaN           NaN           NaN   
CAPITAL AND RESERVES                        NaN           NaN           NaN   
Issued Share Capital                        NaN           NaN           NaN   
Share Premium                               NaN           NaN           NaN   
Other Components Of Equity                  NaN           NaN           NaN   
Treasury Shares                             NaN           NaN           NaN   
Retained Earnings                           NaN           NaN           NaN   
Capital And Reserves                        NaN           NaN           NaN   
NON CURRENT LIABILITIES                     NaN           NaN           NaN   
Loans                                       NaN           NaN           NaN   
Intercompany Loans                          NaN           NaN           NaN   
Deferred Taxation                           NaN           NaN           NaN   
Non Current Liabilities                     NaN           NaN           NaN   
CURRENT LIABILITIES                         NaN           NaN           NaN   
Trade Payables                              NaN           NaN           NaN   
Other Payables                              NaN           NaN           NaN   
Borrowings                                  NaN           NaN           NaN   
Provision For Taxation                     0.00          0.00          0.00   
Provisions                             7,320.00      8,160.00      7,488.00   
Current Liabilities                         NaN           NaN           NaN   
TOTAL EQUITY AND LIABILITIES                NaN           NaN           NaN   
CHECK                                       NaN           NaN           NaN   

                                         Dec-2023      Jan-2024      Feb-2024  \
STATEMENT_OF_FINANCIAL_POSITION                                                 
ASSETS                                        NaN           NaN           NaN   
NON CURRENT ASSETS                            NaN           NaN           NaN   
Property Plant And Equipment           512,229.94    504,833.67    497,940.56   
Intangible Assets                             NaN           NaN           NaN 

### **Generate Borrowings Schedules**

In [102]:
short_term_borrowings_schedules['outstanding_balance_at_start']

Dec-2022   Jan-2023   Feb-2023   Mar-2023   Apr-2023  \
FCB                          0.00       0.00       0.00       0.00 120,383.84   
Zimnat Life Assurance   20,000.00  20,000.00  20,000.00  20,000.00  20,000.00   
Grandre                100,000.00 100,000.00 100,000.00 100,000.00 100,000.00   
FCB                          0.00       0.00       0.00       0.00  18,429.93   
NURTURE                500,000.00 500,000.00 500,000.00 500,000.00 500,000.00   
NMB                          0.00 450,000.00 450,000.00 450,000.00 450,000.00   
DANDEMUTANDE                 0.00       0.00       0.00  25,000.00  25,000.00   
ZIMNAT LIFE ASSURANCE        0.00       0.00       0.00       0.00  50,000.00   

                         May-2023   Jun-2023   Jul-2023   Aug-2023   Sep-2023  \
FCB                    120,383.84 120,383.84       0.00       0.00       0.00   
Zimnat Life Assurance   20,000.00  20,000.00  20,000.00  20,000.00  20,000.00   
Grandre                100,000.00 100,000.00 100,000.00 100,000.00 100,000.00   
FCB                     18,429.93  18,429.93  18,429.93  18,429.93  18,429.93   
NURTURE                500,000.00 500,000.00 500,000.00 500,000.00 500,000.00   
NMB                    450,000.00 450,000.00 450,000.00 450,000.00 450,000.00   
DANDEMUTANDE            25,000.00  25,000.00  25,000.00  25,000.00  25,000.00   
ZIMNAT LIFE ASSURANCE   41,892.48  33,695.95  25,409.43  17,031.93   8,562.46   

                         Oct-2023   Nov-2023   Dec-2023  Jan-2024  Feb-2024  
FCB                          0.00       0.00       0.00      0.00      0.00  
Zimnat Life Assurance   20,000.00  20,000.00       0.00      0.00      0.00  
Grandre                100,000.00 100,000.00       0.00      0.00      0.00  
FCB                     18,429.93  18,429.93  18,429.93 18,429.93 18,429.93  
NURTURE                500,000.00 500,000.00       0.00      0.00      0.00  
NMB                    450,000.00 450,000.00 450,000.00      0.00      0.00  
DANDEMUTANDE            25,000.00  25,000.00  25,000.00 25,000.00 25,000.00  
ZIMNAT LIFE ASSURANCE        0.00       0.00       0.00      0.00      0.00

In [103]:
short_term_borrowings_schedules_outstanding_balances_df

Dec-2022   Jan-2023   Feb-2023   Mar-2023   Apr-2023  \
FCB                          0.00       0.00       0.00       0.00 120,383.84   
Zimnat Life Assurance   20,000.00  20,000.00  20,000.00  20,000.00  20,000.00   
Grandre                100,000.00 100,000.00 100,000.00 100,000.00 100,000.00   
FCB                          0.00       0.00       0.00       0.00  18,429.93   
NURTURE                500,000.00 500,000.00 500,000.00 500,000.00 500,000.00   
NMB                          0.00 450,000.00 450,000.00 450,000.00 450,000.00   
DANDEMUTANDE                 0.00       0.00       0.00  25,000.00  25,000.00   
ZIMNAT LIFE ASSURANCE        0.00       0.00       0.00       0.00  50,000.00   

                         May-2023   Jun-2023   Jul-2023   Aug-2023   Sep-2023  \
FCB                    120,383.84 120,383.84       0.00       0.00       0.00   
Zimnat Life Assurance   20,000.00  20,000.00  20,000.00  20,000.00  20,000.00   
Grandre                100,000.00 100,000.00 100,000.00 100,000.00 100,000.00   
FCB                     18,429.93  18,429.93  18,429.93  18,429.93  18,429.93   
NURTURE                500,000.00 500,000.00 500,000.00 500,000.00 500,000.00   
NMB                    450,000.00 450,000.00 450,000.00 450,000.00 450,000.00   
DANDEMUTANDE            25,000.00  25,000.00  25,000.00  25,000.00  25,000.00   
ZIMNAT LIFE ASSURANCE   41,892.48  33,695.95  25,409.43  17,031.93   8,562.46   

                         Oct-2023   Nov-2023   Dec-2023  Jan-2024  Feb-2024  
FCB                          0.00       0.00       0.00      0.00      0.00  
Zimnat Life Assurance   20,000.00  20,000.00       0.00      0.00      0.00  
Grandre                100,000.00 100,000.00       0.00      0.00      0.00  
FCB                     18,429.93  18,429.93  18,429.93 18,429.93 18,429.93  
NURTURE                500,000.00 500,000.00       0.00      0.00      0.00  
NMB                    450,000.00 450,000.00 450,000.00      0.00      0.00  
DANDEMUTANDE            25,000.00  25,000.00  25,000.00 25,000.00 25,000.00  
ZIMNAT LIFE ASSURANCE        0.00       0.00       0.00      0.00      0.00

In [104]:
short_term_borrowings_schedules['capital_repayments']

Apr-2023  May-2023  Jun-2023   Jul-2023  Aug-2023  \
FCB                         0.00      0.00      0.00 120,383.84      0.00   
Zimnat Life Assurance       0.00      0.00      0.00       0.00      0.00   
Grandre                     0.00      0.00      0.00       0.00      0.00   
FCB                         0.00      0.00      0.00       0.00      0.00   
NURTURE                     0.00      0.00      0.00       0.00      0.00   
NMB                         0.00      0.00      0.00       0.00      0.00   
DANDEMUTANDE                0.00      0.00      0.00       0.00      0.00   
ZIMNAT LIFE ASSURANCE   8,107.52  8,196.53  8,286.52   8,377.50  8,469.47   

                        Sep-2023  Oct-2023  Nov-2023   Dec-2023   Jan-2024  \
FCB                         0.00       NaN       NaN       0.00       0.00   
Zimnat Life Assurance       0.00       NaN       NaN  20,000.00       0.00   
Grandre                     0.00       NaN       NaN 100,000.00       0.00   
FCB                         0.00       NaN       NaN       0.00       0.00   
NURTURE                     0.00       NaN       NaN 500,000.00       0.00   
NMB                         0.00       NaN       NaN       0.00 450,000.00   
DANDEMUTANDE                0.00       NaN       NaN       0.00       0.00   
ZIMNAT LIFE ASSURANCE   8,562.46       NaN       NaN       0.00       0.00   

                        Feb-2024  Mar-2024  
FCB                          NaN      0.00  
Zimnat Life Assurance        NaN      0.00  
Grandre                      NaN      0.00  
FCB                          NaN      0.00  
NURTURE                      NaN      0.00  
NMB                          NaN      0.00  
DANDEMUTANDE                 NaN 25,000.00  
ZIMNAT LIFE ASSURANCE        NaN      0.00

In [105]:
short_term_borrowings_schedules_outstanding_balances_df.sum()

Dec-2022     620,000.00
Jan-2023   1,070,000.00
Feb-2023   1,070,000.00
Mar-2023   1,095,000.00
Apr-2023   1,283,813.77
May-2023   1,275,706.25
Jun-2023   1,267,509.72
Jul-2023   1,138,839.36
Aug-2023   1,130,461.86
Sep-2023   1,121,992.39
Oct-2023   1,113,429.93
Nov-2023   1,113,429.93
Dec-2023     493,429.93
Jan-2024      43,429.93
Feb-2024      43,429.93
dtype: float64

In [106]:
short_term_loans_schedules = balance_sheet.calculate_short_term_loans_schedules(
    long_and_short_term_borrowing_df=long_and_short_term_borrowing_df,
    capital_repayment_on_borrowings_df=short_term_borrowings_schedules[
        "capital_repayments"
    ].sum(),
    opening_balance_on_short_term_loans=short_term_borrowings_schedules_outstanding_balances_df.sum()[
        (pd.Timestamp(start_date) - pd.DateOffset(months=1)).strftime("%b-%Y")
    ],
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)

short_term_loans_schedules

Sep-2023     Oct-2023     Nov-2023     Dec-2023  \
Opening Balance 1,130,461.86 1,121,899.40 1,121,899.40 1,121,899.40   
Borrowings              0.00         0.00         0.00         0.00   
Repayments         -8,562.46        -0.00        -0.00  -620,000.00   
Closing Balance 1,121,899.40 1,121,899.40 1,121,899.40   501,899.40   

                   Jan-2024  Feb-2024   Mar-2024  Apr-2024  May-2024  \
Opening Balance  501,899.40 51,899.40  51,899.40 26,899.40 26,899.40   
Borrowings             0.00      0.00       0.00      0.00      0.00   
Repayments      -450,000.00     -0.00 -25,000.00         0         0   
Closing Balance   51,899.40 51,899.40  26,899.40 26,899.40 26,899.40   

                 Jun-2024  Jul-2024  Aug-2024  Sep-2024  Oct-2024  Nov-2024  \
Opening Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   
Borrowings           0.00      0.00      0.00      0.00      0.00      0.00   
Repayments              0         0         0         0         0         0   
Closing Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   

                 Dec-2024  Jan-2025  Feb-2025  Mar-2025  Apr-2025  May-2025  \
Opening Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   
Borrowings           0.00      0.00      0.00      0.00      0.00      0.00   
Repayments              0         0         0         0         0         0   
Closing Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   

                 Jun-2025  Jul-2025  Aug-2025  Sep-2025  Oct-2025  Nov-2025  \
Opening Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   
Borrowings           0.00      0.00      0.00      0.00      0.00      0.00   
Repayments              0         0         0         0         0         0   
Closing Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   

                 Dec-2025  Jan-2026  Feb-2026  Mar-2026  Apr-2026  May-2026  \
Opening Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   
Borrowings           0.00      0.00      0.00      0.00      0.00      0.00   
Repayments              0         0         0         0         0         0   
Closing Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   

                 Jun-2026  Jul-2026  Aug-2026  Sep-2026  Oct-2026  Nov-2026  \
Opening Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   
Borrowings           0.00      0.00      0.00      0.00      0.00      0.00   
Repayments              0         0         0         0         0         0   
Closing Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   

                 Dec-2026  Jan-2027  Feb-2027  Mar-2027  Apr-2027  May-2027  \
Opening Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   
Borrowings           0.00      0.00      0.00      0.00      0.00      0.00   
Repayments              0         0         0         0         0         0   
Closing Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   

                 Jun-2027  Jul-2027  Aug-2027  Sep-2027  Oct-2027  Nov-2027  \
Opening Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   
Borrowings           0.00      0.00      0.00      0.00      0.00      0.00   
Repayments              0         0         0         0         0         0   
Closing Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   

                 Dec-2027  Jan-2028  Feb-2028  Mar-2028  Apr-2028  May-2028  \
Opening Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   
Borrowings           0.00      0.00      0.00      0.00      0.00      0.00   
Repayments              0         0         0         0         0         0   
Closing Balance 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40 26,899.40   

                 Jun-2028  Jul-2028  Aug-2028  
Opening Balance 26,899.40 26,899.40 26,899.40  
Borrowings           0.00      0.00    

In [107]:
long_term_loans_schedules = balance_sheet.calculate_long_term_loans_schedules(
    long_and_short_term_borrowing_df=long_and_short_term_borrowing_df,
    capital_repayment_on_borrowings_df=long_term_borrowings_schedules[
        "capital_repayments"
    ].sum(),
    opening_balance_on_long_term_loans=long_term_borrowings_schedules_outstanding_balances_df.sum()[
        pd.Timestamp(start_date).strftime("%b-%Y")
    ],
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)

long_term_loans_schedules

Sep-2023     Oct-2023     Nov-2023     Dec-2023  \
Opening Balance 1,198,631.36 1,191,763.72 1,184,855.63 1,177,906.83   
Borrowings                 0            0            0            0   
Repayments         -6,867.64    -6,908.08    -6,948.81  -274,364.80   
Closing Balance 1,191,763.72 1,184,855.63 1,177,906.83   903,542.03   

                  Jan-2024   Feb-2024   Mar-2024   Apr-2024   May-2024  \
Opening Balance 903,542.03 896,510.95 889,438.32 852,323.84 845,167.25   
Borrowings               0          0          0          0          0   
Repayments       -7,031.08  -7,072.63 -37,114.47  -7,156.60  -7,199.01   
Closing Balance 896,510.95 889,438.32 852,323.84 845,167.25 837,968.24   

                  Jun-2024   Jul-2024   Aug-2024   Sep-2024   Oct-2024  \
Opening Balance 837,968.24 830,726.53 823,441.84 816,113.85 808,742.28   
Borrowings               0          0          0          0          0   
Repayments       -7,241.71  -7,284.70  -7,327.99  -7,371.57  -7,415.45   
Closing Balance 830,726.53 823,441.84 816,113.85 808,742.28 801,326.83   

                  Nov-2024   Dec-2024   Jan-2025   Feb-2025   Mar-2025  \
Opening Balance 801,326.83 793,867.19 786,363.07 778,814.15 771,220.13   
Borrowings               0          0          0          0          0   
Repayments       -7,459.64  -7,504.12  -7,548.92  -7,594.02  -7,639.44   
Closing Balance 793,867.19 786,363.07 778,814.15 771,220.13 763,580.69   

                  Apr-2025   May-2025   Jun-2025   Jul-2025   Aug-2025  \
Opening Balance 763,580.69 755,895.53 749,593.04 743,259.87 736,895.87   
Borrowings               0          0          0          0          0   
Repayments       -7,685.16  -6,302.49  -6,333.17  -6,364.00  -6,394.97   
Closing Balance 755,895.53 749,593.04 743,259.87 736,895.87 730,500.90   

                   Sep-2025   Oct-2025   Nov-2025    Dec-2025   Jan-2026  \
Opening Balance  730,500.90 360,074.80 353,617.42  347,128.61 165,608.21   
Borrowings                0          0          0           0          0   
Repayments      -370,426.10  -6,457.38  -6,488.81 -181,520.40  -6,552.13   
Closing Balance  360,074.80 353,617.42 347,128.61  165,608.21 159,056.08   

                  Feb-2026   Mar-2026   Apr-2026   May-2026   Jun-2026  \
Opening Balance 159,056.08 152,472.05 145,855.97 139,207.69 132,527.05   
Borrowings               0          0          0          0          0   
Repayments       -6,584.03  -6,616.08  -6,648.28  -6,680.64  -6,713.16   
Closing Balance 152,472.05 145,855.97 139,207.69 132,527.05 125,813.89   

                  Jul-2026   Aug-2026   Sep-2026   Oct-2026  Nov-2026  \
Opening Balance 125,813.89 119,068.06 112,289.39 105,477.72 98,632.90   
Borrowings               0          0          0          0         0   
Repayments       -6,745.84  -6,778.67  -6,811.67  -6,844.82 -6,878.14   
Closing Balance 119,068.06 112,289.39 105,477.72  98,632.90 91,754.76   

                 Dec-2026  Jan-2027  Feb-2027  Mar-2027  Apr-2027  May-2027  \
Opening Balance 91,754.76 84,843.14 77,897.87 70,918.80 63,905.76 56,858.59   
Borrowings              0         0         0         0         0         0   
Repayments      -6,911.62 -6,945.26 -6,979.07 -7,013.04 -7,047.18 -7,081.48   
Closing Balance 84,843.14 77,897.87 70,918.80 63,905.76 56,858.59 49,777.11   

                 Jun-2027  Jul-2027  Aug-2027  Sep-2027  Oct-2027  Nov-2027  \
Opening Balance 49,777.11 42,769.26 35,727.30 28,651.06 21,540.38 14,395.09   
Borrowings              0         0         0         0         0         0   
Repayments      -7,007.85 -7,041.96 -7,076.24 -7,110.68 -7,145.29 -7,180.07   
Closing Balance 42,769.26 35,727.30 28,651.06 21,540.38 14,395.09  7,215.02   

                Dec-2027 Jan-2028 Feb-2028 Mar-2028 Apr-2028 May-2028  \
Opening Balance 7,215.02 7,215.02 7,215.02 7,215.02 7,215.02 7,215.02   
Borrowings             0        0        0        0        0        0   
Repayments           NaN      NaN      NaN      NaN

### **Insert Borrowings and Loans**


In [108]:
balance_sheet_df.loc["Loans"] = long_term_borrowings_schedules_outstanding_balances_df.sum()
balance_sheet_df.loc["Borrowings"]  = short_term_borrowings_schedules_outstanding_balances_df.sum()
balance_sheet_df.loc["Borrowings"].fillna(0, inplace=True)
balance_sheet_df.loc["Loans"].fillna(0,inplace=True)

### **Generate Receivables and Payables Schedules**

In [109]:
trade_receivables_schedule = balance_sheet.generate_receivables_schedule(
    opening_receivables=opening_balances["TRADE_RECEIVABLES"].iat[0],
    receipts_from_receivables=other_parameters.loc["RECEIPTS_FROM_TRADE_RECEIVABLES"],
    new_receivables=other_parameters.loc["NEW_TRADE_RECEIVABLES"],
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)

other_receivables_schedule = balance_sheet.generate_receivables_schedule(
    opening_receivables=opening_balances["OTHER_RECEIVABLES"].iat[0],
    receipts_from_receivables=other_parameters.loc["RECEIPTS_FROM_OTHER_RECEIVABLES"],
    new_receivables=other_parameters.loc["NEW_OTHER_RECEIVABLES"],
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)

intergroup_receivables_schedule = balance_sheet.generate_receivables_schedule(
    opening_receivables=opening_balances["INTERGROUP_RECEIVABLES"].iat[0],
    receipts_from_receivables=other_parameters.loc["RECEIPTS_FROM_INTERGROUP_RECEIVABLES"],
    new_receivables=other_parameters.loc["NEW_INTERGROUP_RECEIVABLES"],
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)

trade_payables_schedule = balance_sheet.generate_payables_schedule(
    opening_payables=opening_balances["TRADE_PAYABLES"].iat[0],
    payments_to_payables=other_parameters.loc["PAYMENTS_TO_TRADE_PAYABLES"],
    new_payables=other_parameters.loc["NEW_TRADE_PAYABLES"],
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)

other_payables_schedule = balance_sheet.generate_payables_schedule(
    opening_payables=opening_balances["OTHER_PAYABLES"].iat[0],
    payments_to_payables=other_parameters.loc["PAYMENTS_TO_OTHER_PAYABLES"],
    new_payables=other_parameters.loc["NEW_OTHER_PAYABLES"],
    months_to_forecast=months_to_forecast,
    start_date=start_date,
)

balance_sheet_df.loc["Trade Payables"] = trade_payables_schedule.loc["Closing Balance"]
balance_sheet_df.loc["Other Payables"] = other_payables_schedule.loc["Closing Balance"]

balance_sheet_df.loc["Trade Receivables"] = trade_receivables_schedule.loc[
    "Closing Balance"
]

balance_sheet_df.loc["Other Receivables"] = other_receivables_schedule.loc[
    "Closing Balance"
]

balance_sheet_df.loc["Intergroup Receivables"] = intergroup_receivables_schedule.loc[
    "Closing Balance"
]


balance_sheet_df

Sep-2023      Oct-2023      Nov-2023  \
STATEMENT_OF_FINANCIAL_POSITION                                                
ASSETS                                       NaN           NaN           NaN   
NON CURRENT ASSETS                           NaN           NaN           NaN   
Property Plant And Equipment          535,792.44    527,604.97    519,917.46   
Intangible Assets                            NaN           NaN           NaN   
Investment In Subsidiaries                   NaN           NaN           NaN   
Investment In Associates                     NaN           NaN           NaN   
Investment Properties                        NaN           NaN           NaN   
Equity Investments                           NaN           NaN           NaN   
Long Term Money Market Investments           NaN           NaN           NaN   
Loans To Related Entities                    NaN           NaN           NaN   
Non Current Assets                           NaN           NaN           NaN   
CURRENT ASSETS                               NaN           NaN           NaN   
Inventories                                  NaN           NaN           NaN   
Intergroup Receivables                         0             0             0   
Loan Book                             661,432.67  1,238,873.01  1,900,818.08   
Trade Receivables                   1,092,458.00  1,183,683.40  1,241,322.76   
Other Receivables                              0             0             0   
Cash On Hand                         -388,156.48 -1,073,590.26 -1,832,422.70   
Short Term Money Market Investments          NaN           NaN           NaN   
Current Assets                               NaN           NaN           NaN   
TOTAL ASSETS                                 NaN           NaN           NaN   
EQUITY AND LIABILITIES                       NaN           NaN           NaN   
CAPITAL AND RESERVES                         NaN           NaN           NaN   
Issued Share Capital                         NaN           NaN           NaN   
Share Premium                                NaN           NaN           NaN   
Other Components Of Equity                   NaN           NaN           NaN   
Treasury Shares                              NaN           NaN           NaN   
Retained Earnings                            NaN           NaN           NaN   
Capital And Reserves                         NaN           NaN           NaN   
NON CURRENT LIABILITIES                      NaN           NaN           NaN   
Loans                               1,198,631.36  1,191,763.72  1,184,855.63   
Intercompany Loans                           NaN           NaN           NaN   
Deferred Taxation                            NaN           NaN           NaN   
Non Current Liabilities                      NaN           NaN           NaN   
CURRENT LIABILITIES                          NaN           NaN           NaN   
Trade Payables                        938,595.00    925,190.28    856,403.63   
Other Payables                                 0             0             0   
Borrowings                          1,121,992.39  1,113,429.93  1,113,429.93   
Provision For Taxation                      0.00          0.00          0.00   
Provisions                              7,320.00      8,160.00      7,488.00   
Current Liabilities                          NaN           NaN           NaN   
TOTAL EQUITY AND LIABILITIES                 NaN           NaN           NaN   
CHECK                                        NaN           NaN           NaN   

                                         Dec-2023      Jan-2024      Feb-2024  \
STATEMENT_OF_FINANCIAL_POSITION                                                 
ASSETS                                        NaN           NaN           NaN   
NON CURRENT ASSETS                            NaN           NaN           NaN   
Property Plant And Equipment           512,229.94    504,833.67    497,940.56   
Intangible Assets                 

In [110]:
balance_sheet_df.loc['Deferred Taxation'] = tax_schedule.loc['Closing Balance']

In [111]:
inventories_schedule = balance_sheet.generate_inventories_schedule(
    opening_inventories=opening_balances["INVENTORIES"].iat[0],
    new_inventories=other_parameters.loc["NEW_INVENTORY"],
    inventories_used=other_parameters.loc["INVENTORY_USED"],
    start_date=start_date,
    months_to_forecast=months_to_forecast,
)

inventories_schedule

Sep-2023  Oct-2023  Nov-2023  Dec-2023  Jan-2024  Feb-2024  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Mar-2024  Apr-2024  May-2024  Jun-2024  Jul-2024  Aug-2024  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Sep-2024  Oct-2024  Nov-2024  Dec-2024  Jan-2025  Feb-2025  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Mar-2025  Apr-2025  May-2025  Jun-2025  Jul-2025  Aug-2025  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Sep-2025  Oct-2025  Nov-2025  Dec-2025  Jan-2026  Feb-2026  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Mar-2026  Apr-2026  May-2026  Jun-2026  Jul-2026  Aug-2026  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Sep-2026  Oct-2026  Nov-2026  Dec-2026  Jan-2027  Feb-2027  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Mar-2027  Apr-2027  May-2027  Jun-2027  Jul-2027  Aug-2027  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Sep-2027  Oct-2027  Nov-2027  Dec-2027  Jan-2028  Feb-2028  \
Opening Balance          0         0         0         0         0         0   
New Inventories          0         0         0         0         0         0   
Inventories Used         0         0         0         0         0         0   
Closing Balance          0         0         0         0         0         0   

                  Mar-2028  Apr-2028  May-2028  Jun-2028  Jul-2028  Aug-2028  
Opening Balance          0         0         0         0         0         0  
New Inventories          0         0         0         0         0         0  
Inventories Used         0         0         0         0         0         0  
Closing Balance          0         0         0         0         0         0

In [112]:
balance_sheet_df.loc['Inventories']  = inventories_schedule.loc['Closing Balance']

### **Equity and Intercompany Loans**


In [113]:
balance_sheet_df.loc["Issued Share Capital"] = helper.change_period_index_to_strftime(
    other_parameters.loc["SHARE_CAPITAL"].cumsum()
    + opening_balances["ISSUED_SHARE_CAPITAL"].iat[0]
)

balance_sheet_df.loc["Intercompany Loans"] = helper.change_period_index_to_strftime(
    other_parameters.loc["INTERCOMPANY_LOANS"].cumsum()
    + opening_balances["INTERCOMPANY_LOANS"].iat[0]
)


balance_sheet_df.loc["Share Premium"] = helper.change_period_index_to_strftime(
    other_parameters.loc["SHARE_PREMIUM"].cumsum() + opening_balances["SHARE_PREMIUM"].iat[0]
)

balance_sheet_df.loc[
    "Other Components Of Equity"
] = helper.change_period_index_to_strftime(
    other_parameters.loc["OTHER_COMPONENTS_OF_EQUITY"].cumsum()
    + opening_balances["OTHER_COMPONENTS_OF_EQUITY"].iat[0]
)

balance_sheet_df.loc["Treasury Shares"] = helper.change_period_index_to_strftime(
    other_parameters.loc["TREASURY_SHARES"].cumsum()
    + opening_balances["TREASURY_SHARES"].iat[0]
)

balance_sheet_df.loc["Retained Earnings"] = (
    income_statement_df.loc["PROFIT/(LOSS) FOR PERIOD"]
    - helper.change_period_index_to_strftime(other_parameters.loc["DIVIDEND_PAID"])
).cumsum()

balance_sheet_df.loc["Capital And Reserves"] = balance_sheet_df.loc[
    "Issued Share Capital":"Retained Earnings"
].sum()

### **Other Assets**

In [114]:
balance_sheet_df.loc["Intangible Assets"] = helper.change_period_index_to_strftime(
    other_parameters.loc["INTANGIBLE_ASSETS"].cumsum()
    + opening_balances["INTANGIBLE_ASSETS"].iat[0]
)

balance_sheet_df.loc[
    "Investment In Subsidiaries"
] = helper.change_period_index_to_strftime(
    other_parameters.loc["INVESTMENT_IN_SUBSIDIARIES"].cumsum()
    + opening_balances["INVESTMENT_IN_SUBSIDIARIES"].iat[0]
)

balance_sheet_df.loc[
    "Investment In Associates"
] = helper.change_period_index_to_strftime(
    other_parameters.loc["INVESTMENT_IN_ASSOCIATES"].cumsum()
    + opening_balances["INVESTMENT_IN_ASSOCIATES"].iat[0]
)

balance_sheet_df.loc["Investment Properties"] = helper.change_period_index_to_strftime(
    other_parameters.loc["INVESTMENT_PROPERTIES"].cumsum()
    + opening_balances["INVESTMENT_PROPERTIES"].iat[0]
)

balance_sheet_df.loc["Equity Investments"] = helper.change_period_index_to_strftime(
    other_parameters.loc["EQUITY_INVESTMENTS"].cumsum()
    + opening_balances["EQUITY_INVESTMENTS"].iat[0]
)

balance_sheet_df.loc[
    "Long Term Money Market Investments"
] = helper.change_period_index_to_strftime(
    other_parameters.loc["LONG_TERM_MONEY_MARKET_INVESTMENTS"].cumsum()
    + opening_balances["LONG_TERM_MONEY_MARKET_INVESTMENTS"].iat[0]
)

balance_sheet_df.loc[
    "Short Term Money Market Investments"
] = helper.change_period_index_to_strftime(
    other_parameters.loc["SHORT_TERM_MONEY_MARKET_INVESTMENTS"].cumsum()
    + opening_balances["SHORT_TERM_MONEY_MARKET_INVESTMENTS"].iat[0]
)

balance_sheet_df.loc[
    "Loans To Related Entities"
] = helper.change_period_index_to_strftime(
    other_parameters.loc["LOANS_TO_RELATED_ENTITIES"].cumsum()
    + opening_balances["LOANS_TO_RELATED_ENTITIES"].iat[0]
)

In [115]:
balance_sheet_df

Sep-2023      Oct-2023      Nov-2023  \
STATEMENT_OF_FINANCIAL_POSITION                                                
ASSETS                                       NaN           NaN           NaN   
NON CURRENT ASSETS                           NaN           NaN           NaN   
Property Plant And Equipment          535,792.44    527,604.97    519,917.46   
Intangible Assets                           0.00          0.00          0.00   
Investment In Subsidiaries                  0.00          0.00          0.00   
Investment In Associates                    0.00          0.00          0.00   
Investment Properties                       0.00          0.00          0.00   
Equity Investments                          0.00          0.00          0.00   
Long Term Money Market Investments          0.00          0.00          0.00   
Loans To Related Entities                   0.00          0.00          0.00   
Non Current Assets                           NaN           NaN           NaN   
CURRENT ASSETS                               NaN           NaN           NaN   
Inventories                                    0             0             0   
Intergroup Receivables                         0             0             0   
Loan Book                             661,432.67  1,238,873.01  1,900,818.08   
Trade Receivables                   1,092,458.00  1,183,683.40  1,241,322.76   
Other Receivables                              0             0             0   
Cash On Hand                         -388,156.48 -1,073,590.26 -1,832,422.70   
Short Term Money Market Investments         0.00          0.00          0.00   
Current Assets                               NaN           NaN           NaN   
TOTAL ASSETS                                 NaN           NaN           NaN   
EQUITY AND LIABILITIES                       NaN           NaN           NaN   
CAPITAL AND RESERVES                         NaN           NaN           NaN   
Issued Share Capital                    7,050.00      6,130.46      5,222.28   
Share Premium                             110.00         95.65         81.48   
Other Components Of Equity             59,784.00     59,784.00     59,784.00   
Treasury Shares                             0.00          0.00          0.00   
Retained Earnings                    -142,416.83   -230,914.82   -262,058.75   
Capital And Reserves                  -75,472.83   -164,904.70   -196,970.99   
NON CURRENT LIABILITIES                      NaN           NaN           NaN   
Loans                               1,198,631.36  1,191,763.72  1,184,855.63   
Intercompany Loans                          0.00          0.00          0.00   
Deferred Taxation                           0.00          0.00          0.00   
Non Current Liabilities                      NaN           NaN           NaN   
CURRENT LIABILITIES                          NaN           NaN           NaN   
Trade Payables                        938,595.00    925,190.28    856,403.63   
Other Payables                                 0             0             0   
Borrowings                          1,121,992.39  1,113,429.93  1,113,429.93   
Provision For Taxation                      0.00          0.00          0.00   
Provisions                              7,320.00      8,160.00      7,488.00   
Current Liabilities                          NaN           NaN           NaN   
TOTAL EQUITY AND LIABILITIES                 NaN           NaN           NaN   
CHECK                                        NaN           NaN           NaN   

                                         Dec-2023      Jan-2024      Feb-2024  \
STATEMENT_OF_FINANCIAL_POSITION                                                 
ASSETS                                        NaN           NaN           NaN   
NON CURRENT ASSETS                            NaN           NaN           NaN   
Property Plant And Equipment           512,229.94    504,833.67    497,940.56   
Intangible Assets                 

### **Calculate Totals**


In [116]:
balance_sheet_df = balance_sheet.sum_financial_statements_totals(balance_sheet_df)
balance_sheet_df = balance_sheet.calculate_final_balances(balance_sheet_df=balance_sheet_df)
balance_sheet_df

Sep-2023      Oct-2023      Nov-2023  \
STATEMENT_OF_FINANCIAL_POSITION                                                
ASSETS                                       NaN           NaN           NaN   
NON CURRENT ASSETS                           NaN           NaN           NaN   
Property Plant And Equipment          535,792.44    527,604.97    519,917.46   
Intangible Assets                           0.00          0.00          0.00   
Investment In Subsidiaries                  0.00          0.00          0.00   
Investment In Associates                    0.00          0.00          0.00   
Investment Properties                       0.00          0.00          0.00   
Equity Investments                          0.00          0.00          0.00   
Long Term Money Market Investments          0.00          0.00          0.00   
Loans To Related Entities                   0.00          0.00          0.00   
Non Current Assets                    535,792.44    527,604.97    519,917.46   
CURRENT ASSETS                               NaN           NaN           NaN   
Inventories                                    0             0             0   
Intergroup Receivables                         0             0             0   
Loan Book                             661,432.67  1,238,873.01  1,900,818.08   
Trade Receivables                   1,092,458.00  1,183,683.40  1,241,322.76   
Other Receivables                              0             0             0   
Cash On Hand                         -388,156.48 -1,073,590.26 -1,832,422.70   
Short Term Money Market Investments         0.00          0.00          0.00   
Current Assets                      1,365,734.20  1,348,966.14  1,309,718.14   
TOTAL ASSETS                        1,901,526.63  1,876,571.12  1,829,635.59   
EQUITY AND LIABILITIES                       NaN           NaN           NaN   
CAPITAL AND RESERVES                         NaN           NaN           NaN   
Issued Share Capital                    7,050.00      6,130.46      5,222.28   
Share Premium                             110.00         95.65         81.48   
Other Components Of Equity             59,784.00     59,784.00     59,784.00   
Treasury Shares                             0.00          0.00          0.00   
Retained Earnings                    -142,416.83   -230,914.82   -262,058.75   
Capital And Reserves                  -75,472.83   -164,904.70   -196,970.99   
NON CURRENT LIABILITIES                      NaN           NaN           NaN   
Loans                               1,198,631.36  1,191,763.72  1,184,855.63   
Intercompany Loans                          0.00          0.00          0.00   
Deferred Taxation                           0.00          0.00          0.00   
Non Current Liabilities             1,198,631.36  1,191,763.72  1,184,855.63   
CURRENT LIABILITIES                          NaN           NaN           NaN   
Trade Payables                        938,595.00    925,190.28    856,403.63   
Other Payables                                 0             0             0   
Borrowings                          1,121,992.39  1,113,429.93  1,113,429.93   
Provision For Taxation                      0.00          0.00          0.00   
Provisions                              7,320.00      8,160.00      7,488.00   
Current Liabilities                 2,067,907.39  2,046,780.21  1,977,321.56   
TOTAL EQUITY AND LIABILITIES        3,191,065.91  3,073,639.23  2,965,206.20   
CHECK                                      False         False         False   

                                         Dec-2023      Jan-2024      Feb-2024  \
STATEMENT_OF_FINANCIAL_POSITION                                                 
ASSETS                                        NaN           NaN           NaN   
NON CURRENT ASSETS                            NaN           NaN           NaN   
Property Plant And Equipment           512,229.94    504,833.67    497,940.56   
Intangible Assets                 

In [117]:
balance_sheet_yearly_df = balance_sheet.calculate_balance_sheet_yearly(
    balance_sheet_df=balance_sheet_df
)

In [118]:
balance_sheet_df

Sep-2023      Oct-2023      Nov-2023  \
STATEMENT_OF_FINANCIAL_POSITION                                                
ASSETS                                       NaN           NaN           NaN   
NON CURRENT ASSETS                           NaN           NaN           NaN   
Property Plant And Equipment          535,792.44    527,604.97    519,917.46   
Intangible Assets                           0.00          0.00          0.00   
Investment In Subsidiaries                  0.00          0.00          0.00   
Investment In Associates                    0.00          0.00          0.00   
Investment Properties                       0.00          0.00          0.00   
Equity Investments                          0.00          0.00          0.00   
Long Term Money Market Investments          0.00          0.00          0.00   
Loans To Related Entities                   0.00          0.00          0.00   
Non Current Assets                    535,792.44    527,604.97    519,917.46   
CURRENT ASSETS                               NaN           NaN           NaN   
Inventories                                    0             0             0   
Intergroup Receivables                         0             0             0   
Loan Book                             661,432.67  1,238,873.01  1,900,818.08   
Trade Receivables                   1,092,458.00  1,183,683.40  1,241,322.76   
Other Receivables                              0             0             0   
Cash On Hand                         -388,156.48 -1,073,590.26 -1,832,422.70   
Short Term Money Market Investments         0.00          0.00          0.00   
Current Assets                      1,365,734.20  1,348,966.14  1,309,718.14   
TOTAL ASSETS                        1,901,526.63  1,876,571.12  1,829,635.59   
EQUITY AND LIABILITIES                       NaN           NaN           NaN   
CAPITAL AND RESERVES                         NaN           NaN           NaN   
Issued Share Capital                    7,050.00      6,130.46      5,222.28   
Share Premium                             110.00         95.65         81.48   
Other Components Of Equity             59,784.00     59,784.00     59,784.00   
Treasury Shares                             0.00          0.00          0.00   
Retained Earnings                    -142,416.83   -230,914.82   -262,058.75   
Capital And Reserves                  -75,472.83   -164,904.70   -196,970.99   
NON CURRENT LIABILITIES                      NaN           NaN           NaN   
Loans                               1,198,631.36  1,191,763.72  1,184,855.63   
Intercompany Loans                          0.00          0.00          0.00   
Deferred Taxation                           0.00          0.00          0.00   
Non Current Liabilities             1,198,631.36  1,191,763.72  1,184,855.63   
CURRENT LIABILITIES                          NaN           NaN           NaN   
Trade Payables                        938,595.00    925,190.28    856,403.63   
Other Payables                                 0             0             0   
Borrowings                          1,121,992.39  1,113,429.93  1,113,429.93   
Provision For Taxation                      0.00          0.00          0.00   
Provisions                              7,320.00      8,160.00      7,488.00   
Current Liabilities                 2,067,907.39  2,046,780.21  1,977,321.56   
TOTAL EQUITY AND LIABILITIES        3,191,065.91  3,073,639.23  2,965,206.20   
CHECK                                      False         False         False   

                                         Dec-2023      Jan-2024      Feb-2024  \
STATEMENT_OF_FINANCIAL_POSITION                                                 
ASSETS                                        NaN           NaN           NaN   
NON CURRENT ASSETS                            NaN           NaN           NaN   
Property Plant And Equipment           512,229.94    504,833.67    497,940.56   
Intangible Assets                 

## **Indirect Cashflow**

In [119]:
statement_of_cashflow_df = (
    statement_of_cashflows.generate_statement_of_cashflow_template(
        start_date, months_to_forecast
    )
)

### **Insert Available Balances**

In [120]:
statement_of_cashflow_df.loc["Profit/(loss) Per I/S"] = income_statement_df.loc[
    "PROFIT/(LOSS) FOR PERIOD"
]

statement_of_cashflow_df.loc["Depreciation"] = income_statement_df.loc["Depreciation"]
statement_of_cashflow_df.loc["Dividend Paid"] = -helper.change_period_index_to_strftime(
    other_parameters.loc["DIVIDEND_PAID"]
)
statement_of_cashflow_df.loc[
    "Treasury Movements"
] = helper.change_period_index_to_strftime(other_parameters.loc["TREASURY_MOVEMENTS"])
statement_of_cashflow_df.loc[
    "Interest Expense Accrued"
] = helper.change_period_index_to_strftime(
    other_parameters.loc["INTEREST_EXPENSE_ACCRUED"]
)
statement_of_cashflow_df.loc[
    "Other Non-Cash Items"
] = helper.change_period_index_to_strftime(other_parameters.loc["OTHER_NON_CASH_ITEMS"])

statement_of_cashflow_df.loc["Interest Paid"] = -finance_costs_df.loc["total"]

statement_of_cashflow_df.loc["Tax Paid"] = tax_schedule.loc["Tax Paid"]

statement_of_cashflow_df.loc[
    "Repayment Of Borrowings"
] = -capital_repayment_borrowings_df.loc["total"]
statement_of_cashflow_df.loc["Purchase Of Fixed Assets"] = capital_expenses
statement_of_cashflow_df.loc["Increase/(Decrease) In Short Term Borrowings"] = (
    short_term_loans_schedules.loc["Closing Balance"]
    - short_term_loans_schedules.loc["Opening Balance"]
)
statement_of_cashflow_df.loc["Increase/(Decrease) In Long Term Borrowings"] = (
    long_term_loans_schedules.loc["Closing Balance"]
    - long_term_loans_schedules.loc["Opening Balance"]
)
statement_of_cashflow_df

Sep-2023   Oct-2023  \
STATEMENT_OF_CASHFLOWS                                                
Profit/(loss) Per I/S                        -142,416.83 -88,497.99   
Treasury Movements                                  0.00       0.00   
Adjustments For:                                     NaN        NaN   
Depreciation                                    8,187.46   8,187.46   
Interest Expense Accrued                            0.00       0.00   
Other Non-Cash Items                                0.00       0.00   
Cash From Operations Before WC                       NaN        NaN   
Working Capital Movements                            NaN        NaN   
(Increase)/Decrease In Receivables                   NaN        NaN   
Increase/(Decrease) In Payables                      NaN        NaN   
(Increase)/Decrease In Loan Book (Principle)         NaN        NaN   
(Increase)/Decrease In Loan Book (Interest)          NaN        NaN   
Increase/(Decrease) In Borrowings                    NaN        NaN   
Cash From Operations After WC                        NaN        NaN   
Interest Paid                                 -34,829.99 -23,645.54   
Tax Paid                                           -0.00      -0.00   
Net Cash Flow From Operations                        NaN        NaN   
CASH FLOW FROM INVESTING ACTIVITIES                  NaN        NaN   
Purchase Of Fixed Assets                               0          0   
Cash Flow From Investing Activities                  NaN        NaN   
CASH FLOW FROM FINANCING ACTIVITIES                  NaN        NaN   
Increase/(Decrease) In Long Term Borrowings    -6,867.64  -6,908.08   
Increase/(Decrease) In Short Term Borrowings   -8,562.46       0.00   
Repayment Of Borrowings                       -15,430.09  -6,908.08   
Dividend Paid                                      -0.00      -0.00   
Cash Flow From Financing Activities                  NaN        NaN   
Net Increase/(Decrease) In Cash                      NaN        NaN   
Cash At Beginning Of Period                          NaN        NaN   
Cash At End Of Period                                NaN        NaN   

                                               Nov-2023    Dec-2023  \
STATEMENT_OF_CASHFLOWS                                                
Profit/(loss) Per I/S                        -31,143.93   -5,112.90   
Treasury Movements                                 0.00        0.00   
Adjustments For:                                    NaN         NaN   
Depreciation                                   7,687.51    7,687.51   
Interest Expense Accrued                           0.00        0.00   
Other Non-Cash Items                               0.00        0.00   
Cash From Operations Before WC                      NaN         NaN   
Working Capital Movements                           NaN         NaN   
(Increase)/Decrease In Receivables                  NaN         NaN   
Increase/(Decrease) In Payables                     NaN         NaN   
(Increase)/Decrease In Loan Book (Principle)        NaN         NaN   
(Increase)/Decrease In Loan Book (Interest)         NaN         NaN   
Increase/(Decrease) In Borrowings                   NaN         NaN   
Cash From Operations After WC                       NaN         NaN   
Interest Paid                                 -3,354.82  -52,555.32   
Tax Paid                                          -0.00   -4,875.68   
Net Cash Flow From Operations                       NaN         NaN   
CASH FLOW FROM INVESTING ACTIVITIES                 NaN         NaN   
Purchase Of Fixed Assets                              0           0   
Cash Flow From Investing Activities                 NaN         NaN   
CASH FLOW FROM FINANCING ACTIVITIES                 NaN         NaN   
Increase/(Decrease) In Long Term Borrowings   -6,948.81 -274,364.80   
Increase/(Decrease) In Short Term Borrowings       0.00 -620,000.00   
Repayment Of Borrowings                       -6,948.81 -894,364.80   


In [121]:
statement_of_cashflow_df.loc[
    "Cash From Operations Before WC"
] = statement_of_cashflow_df.iloc[
    1 : statement_of_cashflow_df.index.get_loc("Cash From Operations Before WC")
].sum()

In [122]:

statement_of_cashflow_df

Sep-2023   Oct-2023  \
STATEMENT_OF_CASHFLOWS                                                
Profit/(loss) Per I/S                        -142,416.83 -88,497.99   
Treasury Movements                                  0.00       0.00   
Adjustments For:                                     NaN        NaN   
Depreciation                                    8,187.46   8,187.46   
Interest Expense Accrued                            0.00       0.00   
Other Non-Cash Items                                0.00       0.00   
Cash From Operations Before WC                  8,187.46   8,187.46   
Working Capital Movements                            NaN        NaN   
(Increase)/Decrease In Receivables                   NaN        NaN   
Increase/(Decrease) In Payables                      NaN        NaN   
(Increase)/Decrease In Loan Book (Principle)         NaN        NaN   
(Increase)/Decrease In Loan Book (Interest)          NaN        NaN   
Increase/(Decrease) In Borrowings                    NaN        NaN   
Cash From Operations After WC                        NaN        NaN   
Interest Paid                                 -34,829.99 -23,645.54   
Tax Paid                                           -0.00      -0.00   
Net Cash Flow From Operations                        NaN        NaN   
CASH FLOW FROM INVESTING ACTIVITIES                  NaN        NaN   
Purchase Of Fixed Assets                               0          0   
Cash Flow From Investing Activities                  NaN        NaN   
CASH FLOW FROM FINANCING ACTIVITIES                  NaN        NaN   
Increase/(Decrease) In Long Term Borrowings    -6,867.64  -6,908.08   
Increase/(Decrease) In Short Term Borrowings   -8,562.46       0.00   
Repayment Of Borrowings                       -15,430.09  -6,908.08   
Dividend Paid                                      -0.00      -0.00   
Cash Flow From Financing Activities                  NaN        NaN   
Net Increase/(Decrease) In Cash                      NaN        NaN   
Cash At Beginning Of Period                          NaN        NaN   
Cash At End Of Period                                NaN        NaN   

                                               Nov-2023    Dec-2023  \
STATEMENT_OF_CASHFLOWS                                                
Profit/(loss) Per I/S                        -31,143.93   -5,112.90   
Treasury Movements                                 0.00        0.00   
Adjustments For:                                    NaN         NaN   
Depreciation                                   7,687.51    7,687.51   
Interest Expense Accrued                           0.00        0.00   
Other Non-Cash Items                               0.00        0.00   
Cash From Operations Before WC                 7,687.51    7,687.51   
Working Capital Movements                           NaN         NaN   
(Increase)/Decrease In Receivables                  NaN         NaN   
Increase/(Decrease) In Payables                     NaN         NaN   
(Increase)/Decrease In Loan Book (Principle)        NaN         NaN   
(Increase)/Decrease In Loan Book (Interest)         NaN         NaN   
Increase/(Decrease) In Borrowings                   NaN         NaN   
Cash From Operations After WC                       NaN         NaN   
Interest Paid                                 -3,354.82  -52,555.32   
Tax Paid                                          -0.00   -4,875.68   
Net Cash Flow From Operations                       NaN         NaN   
CASH FLOW FROM INVESTING ACTIVITIES                 NaN         NaN   
Purchase Of Fixed Assets                              0           0   
Cash Flow From Investing Activities                 NaN         NaN   
CASH FLOW FROM FINANCING ACTIVITIES                 NaN         NaN   
Increase/(Decrease) In Long Term Borrowings   -6,948.81 -274,364.80   
Increase/(Decrease) In Short Term Borrowings       0.00 -620,000.00   
Repayment Of Borrowings                       -6,948.81 -894,364.80   


### **Working Capital Movements**

In [123]:
change_in_receivables = (
    other_receivables_schedule.loc["Closing Balance"]
    - other_receivables_schedule.loc["Opening Balance"]
    + trade_receivables_schedule.loc["Closing Balance"]
    - trade_receivables_schedule.loc["Opening Balance"]
    + intergroup_receivables_schedule.loc["Closing Balance"]
    - intergroup_receivables_schedule.loc["Opening Balance"]
)

change_in_receivables.head()

Sep-2023            0.00
Oct-2023       91,225.40
Nov-2023       57,639.36
Dec-2023       58,279.67
Jan-2024   -1,187,638.92
dtype: float64

In [124]:
change_in_payables = (
    trade_payables_schedule.loc["Closing Balance"]
    - trade_payables_schedule.loc["Opening Balance"]
    + other_payables_schedule.loc["Closing Balance"]
    - other_payables_schedule.loc["Opening Balance"]
)
change_in_payables.head()

Sep-2023          0.00
Oct-2023    -13,404.72
Nov-2023    -68,786.66
Dec-2023    -80,963.15
Jan-2024   -466,687.36
dtype: float64

In [125]:
change_in_loan_book_principle = loan_book_df.loc["New Disbursements":"Repayments"].sum()
change_in_loan_book_principle.head()

Sep-2023   542,729.24
Oct-2023   528,854.39
Nov-2023   566,754.85
Dec-2023   431,537.96
Jan-2024   591,856.57
dtype: object

In [126]:
change_in_loan_book_interest = loan_book_df.loc['Interest Income']
change_in_loan_book_interest.head()

Sep-2023     6,626.19
Oct-2023    48,585.94
Nov-2023    95,190.23
Dec-2023   145,937.14
Jan-2024   184,731.17
Name: Interest Income, dtype: object

In [127]:
borrowings_schedule = long_term_loans_schedules + short_term_loans_schedules
change_in_borrowings = borrowings_schedule.loc['Closing Balance'] - borrowings_schedule.loc['Opening Balance']
change_in_borrowings.head()

Sep-2023    -15,430.09
Oct-2023     -6,908.08
Nov-2023     -6,948.81
Dec-2023   -894,364.80
Jan-2024   -457,031.08
dtype: object

In [128]:
statement_of_cashflow_df.loc['(Increase)/Decrease In Receivables'] = change_in_receivables
statement_of_cashflow_df.loc['Increase/(Decrease) In Payables'] = change_in_payables
statement_of_cashflow_df.loc['(Increase)/Decrease In Loan Book (Principle)'] = change_in_loan_book_principle
statement_of_cashflow_df.loc['(Increase)/Decrease In Loan Book (Interest)'] = change_in_loan_book_interest
statement_of_cashflow_df.loc['Increase/(Decrease) In Borrowings'] = change_in_borrowings

In [129]:
statement_of_cashflow_df.loc["Cash From Operations After WC"] = (
    statement_of_cashflow_df.loc["Cash From Operations Before WC"]
    + statement_of_cashflow_df.iloc[
        statement_of_cashflow_df.index.get_loc("Working Capital Movements")
        + 1 : statement_of_cashflow_df.index.get_loc("Cash From Operations After WC")
    ].sum()
)

In [130]:
statement_of_cashflow_df.loc[
    "Net Cash Flow From Operations"
] = statement_of_cashflow_df.loc["Cash From Operations After WC":"Tax Paid"].sum()

In [131]:
statement_of_cashflow_df

Sep-2023   Oct-2023  \
STATEMENT_OF_CASHFLOWS                                                
Profit/(loss) Per I/S                        -142,416.83 -88,497.99   
Treasury Movements                                  0.00       0.00   
Adjustments For:                                     NaN        NaN   
Depreciation                                    8,187.46   8,187.46   
Interest Expense Accrued                            0.00       0.00   
Other Non-Cash Items                                0.00       0.00   
Cash From Operations Before WC                  8,187.46   8,187.46   
Working Capital Movements                            NaN        NaN   
(Increase)/Decrease In Receivables                  0.00  91,225.40   
Increase/(Decrease) In Payables                     0.00 -13,404.72   
(Increase)/Decrease In Loan Book (Principle)  542,729.24 528,854.39   
(Increase)/Decrease In Loan Book (Interest)     6,626.19  48,585.94   
Increase/(Decrease) In Borrowings             -15,430.09  -6,908.08   
Cash From Operations After WC                 542,112.80 656,540.39   
Interest Paid                                 -34,829.99 -23,645.54   
Tax Paid                                           -0.00      -0.00   
Net Cash Flow From Operations                 507,282.80 632,894.85   
CASH FLOW FROM INVESTING ACTIVITIES                  NaN        NaN   
Purchase Of Fixed Assets                               0          0   
Cash Flow From Investing Activities                  NaN        NaN   
CASH FLOW FROM FINANCING ACTIVITIES                  NaN        NaN   
Increase/(Decrease) In Long Term Borrowings    -6,867.64  -6,908.08   
Increase/(Decrease) In Short Term Borrowings   -8,562.46       0.00   
Repayment Of Borrowings                       -15,430.09  -6,908.08   
Dividend Paid                                      -0.00      -0.00   
Cash Flow From Financing Activities                  NaN        NaN   
Net Increase/(Decrease) In Cash                      NaN        NaN   
Cash At Beginning Of Period                          NaN        NaN   
Cash At End Of Period                                NaN        NaN   

                                               Nov-2023    Dec-2023  \
STATEMENT_OF_CASHFLOWS                                                
Profit/(loss) Per I/S                        -31,143.93   -5,112.90   
Treasury Movements                                 0.00        0.00   
Adjustments For:                                    NaN         NaN   
Depreciation                                   7,687.51    7,687.51   
Interest Expense Accrued                           0.00        0.00   
Other Non-Cash Items                               0.00        0.00   
Cash From Operations Before WC                 7,687.51    7,687.51   
Working Capital Movements                           NaN         NaN   
(Increase)/Decrease In Receivables            57,639.36   58,279.67   
Increase/(Decrease) In Payables              -68,786.66  -80,963.15   
(Increase)/Decrease In Loan Book (Principle) 566,754.85  431,537.96   
(Increase)/Decrease In Loan Book (Interest)   95,190.23  145,937.14   
Increase/(Decrease) In Borrowings             -6,948.81 -894,364.80   
Cash From Operations After WC                651,536.48 -331,885.67   
Interest Paid                                 -3,354.82  -52,555.32   
Tax Paid                                          -0.00   -4,875.68   
Net Cash Flow From Operations                648,181.66 -389,316.67   
CASH FLOW FROM INVESTING ACTIVITIES                 NaN         NaN   
Purchase Of Fixed Assets                              0           0   
Cash Flow From Investing Activities                 NaN         NaN   
CASH FLOW FROM FINANCING ACTIVITIES                 NaN         NaN   
Increase/(Decrease) In Long Term Borrowings   -6,948.81 -274,364.80   
Increase/(Decrease) In Short Term Borrowings       0.00 -620,000.00   
Repayment Of Borrowings                       -6,948.81 -894,364.80   


### **Calculating Totals**

In [132]:
statement_of_cashflow_df = balance_sheet.sum_financial_statements_totals(statement_of_cashflow_df)


statement_of_cashflow_df.loc['Net Increase/(Decrease) In Cash'] = (
    statement_of_cashflow_df.loc["Net Cash Flow From Operations"]
    + statement_of_cashflow_df.loc["Cash Flow From Investing Activities"]
    + statement_of_cashflow_df.loc["Cash Flow From Financing Activities"]
)
statement_of_cashflow_df

Sep-2023   Oct-2023  \
STATEMENT_OF_CASHFLOWS                                                
Profit/(loss) Per I/S                        -142,416.83 -88,497.99   
Treasury Movements                                  0.00       0.00   
Adjustments For:                                     NaN        NaN   
Depreciation                                    8,187.46   8,187.46   
Interest Expense Accrued                            0.00       0.00   
Other Non-Cash Items                                0.00       0.00   
Cash From Operations Before WC                  8,187.46   8,187.46   
Working Capital Movements                            NaN        NaN   
(Increase)/Decrease In Receivables                  0.00  91,225.40   
Increase/(Decrease) In Payables                     0.00 -13,404.72   
(Increase)/Decrease In Loan Book (Principle)  542,729.24 528,854.39   
(Increase)/Decrease In Loan Book (Interest)     6,626.19  48,585.94   
Increase/(Decrease) In Borrowings             -15,430.09  -6,908.08   
Cash From Operations After WC                 542,112.80 656,540.39   
Interest Paid                                 -34,829.99 -23,645.54   
Tax Paid                                           -0.00      -0.00   
Net Cash Flow From Operations                 507,282.80 632,894.85   
CASH FLOW FROM INVESTING ACTIVITIES                  NaN        NaN   
Purchase Of Fixed Assets                               0          0   
Cash Flow From Investing Activities                    0          0   
CASH FLOW FROM FINANCING ACTIVITIES                  NaN        NaN   
Increase/(Decrease) In Long Term Borrowings    -6,867.64  -6,908.08   
Increase/(Decrease) In Short Term Borrowings   -8,562.46       0.00   
Repayment Of Borrowings                       -15,430.09  -6,908.08   
Dividend Paid                                      -0.00      -0.00   
Cash Flow From Financing Activities           -30,860.19 -13,816.17   
Net Increase/(Decrease) In Cash               476,422.61 619,078.69   
Cash At Beginning Of Period                          NaN        NaN   
Cash At End Of Period                                NaN        NaN   

                                               Nov-2023      Dec-2023  \
STATEMENT_OF_CASHFLOWS                                                  
Profit/(loss) Per I/S                        -31,143.93     -5,112.90   
Treasury Movements                                 0.00          0.00   
Adjustments For:                                    NaN           NaN   
Depreciation                                   7,687.51      7,687.51   
Interest Expense Accrued                           0.00          0.00   
Other Non-Cash Items                               0.00          0.00   
Cash From Operations Before WC                 7,687.51      7,687.51   
Working Capital Movements                           NaN           NaN   
(Increase)/Decrease In Receivables            57,639.36     58,279.67   
Increase/(Decrease) In Payables              -68,786.66    -80,963.15   
(Increase)/Decrease In Loan Book (Principle) 566,754.85    431,537.96   
(Increase)/Decrease In Loan Book (Interest)   95,190.23    145,937.14   
Increase/(Decrease) In Borrowings             -6,948.81   -894,364.80   
Cash From Operations After WC                651,536.48   -331,885.67   
Interest Paid                                 -3,354.82    -52,555.32   
Tax Paid                                          -0.00     -4,875.68   
Net Cash Flow From Operations                648,181.66   -389,316.67   
CASH FLOW FROM INVESTING ACTIVITIES                 NaN           NaN   
Purchase Of Fixed Assets                              0             0   
Cash Flow From Investing Activities                   0             0   
CASH FLOW FROM FINANCING ACTIVITIES                 NaN           NaN   
Increase/(Decrease) In Long Term Borrowings   -6,948.81   -274,364.80   
Increase/(Decrease) In Short Term Borrowings       0.00   -620,000.00   
Repayment Of Borrowin

### **Calculating Cash at End and Beginning of Period**

In [133]:
statement_of_cashflow_df = (
    statement_of_cashflows.calculate_cash_at_end_and_beginning_of_period(
        statement_of_cashflow_df=statement_of_cashflow_df,
        opening_balances=opening_balances,
    )
)

statement_of_cashflow_df

Sep-2023     Oct-2023  \
STATEMENT_OF_CASHFLOWS                                                  
Profit/(loss) Per I/S                        -142,416.83   -88,497.99   
Treasury Movements                                  0.00         0.00   
Adjustments For:                                     NaN          NaN   
Depreciation                                    8,187.46     8,187.46   
Interest Expense Accrued                            0.00         0.00   
Other Non-Cash Items                                0.00         0.00   
Cash From Operations Before WC                  8,187.46     8,187.46   
Working Capital Movements                            NaN          NaN   
(Increase)/Decrease In Receivables                  0.00    91,225.40   
Increase/(Decrease) In Payables                     0.00   -13,404.72   
(Increase)/Decrease In Loan Book (Principle)  542,729.24   528,854.39   
(Increase)/Decrease In Loan Book (Interest)     6,626.19    48,585.94   
Increase/(Decrease) In Borrowings             -15,430.09    -6,908.08   
Cash From Operations After WC                 542,112.80   656,540.39   
Interest Paid                                 -34,829.99   -23,645.54   
Tax Paid                                           -0.00        -0.00   
Net Cash Flow From Operations                 507,282.80   632,894.85   
CASH FLOW FROM INVESTING ACTIVITIES                  NaN          NaN   
Purchase Of Fixed Assets                               0            0   
Cash Flow From Investing Activities                    0            0   
CASH FLOW FROM FINANCING ACTIVITIES                  NaN          NaN   
Increase/(Decrease) In Long Term Borrowings    -6,867.64    -6,908.08   
Increase/(Decrease) In Short Term Borrowings   -8,562.46         0.00   
Repayment Of Borrowings                       -15,430.09    -6,908.08   
Dividend Paid                                      -0.00        -0.00   
Cash Flow From Financing Activities           -30,860.19   -13,816.17   
Net Increase/(Decrease) In Cash               476,422.61   619,078.69   
Cash At Beginning Of Period                   331,856.00   808,278.61   
Cash At End Of Period                         808,278.61 1,427,357.30   

                                                 Nov-2023      Dec-2023  \
STATEMENT_OF_CASHFLOWS                                                    
Profit/(loss) Per I/S                          -31,143.93     -5,112.90   
Treasury Movements                                   0.00          0.00   
Adjustments For:                                      NaN           NaN   
Depreciation                                     7,687.51      7,687.51   
Interest Expense Accrued                             0.00          0.00   
Other Non-Cash Items                                 0.00          0.00   
Cash From Operations Before WC                   7,687.51      7,687.51   
Working Capital Movements                             NaN           NaN   
(Increase)/Decrease In Receivables              57,639.36     58,279.67   
Increase/(Decrease) In Payables                -68,786.66    -80,963.15   
(Increase)/Decrease In Loan Book (Principle)   566,754.85    431,537.96   
(Increase)/Decrease In Loan Book (Interest)     95,190.23    145,937.14   
Increase/(Decrease) In Borrowings               -6,948.81   -894,364.80   
Cash From Operations After WC                  651,536.48   -331,885.67   
Interest Paid                                   -3,354.82    -52,555.32   
Tax Paid                                            -0.00     -4,875.68   
Net Cash Flow From Operations                  648,181.66   -389,316.67   
CASH FLOW FROM INVESTING ACTIVITIES                   NaN           NaN   
Purchase Of Fixed Assets                                0             0   
Cash Flow From Investing Activities                     0             0   
CASH FLOW FROM FINANCING ACTIVITIES                   NaN           NaN   
Increase/(Decrease) In Long Term Borrowings     -6,948.81  

In [ ]:
statement_of_cashflow_yearly_df = (
    statement_of_cashflows.calculate_statement_of_cashflow_yearly_df(
        statement_of_cashflow_df=statement_of_cashflow_df,
        opening_balances=opening_balances,
    )
)

statement_of_cashflow_yearly_df